In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import duckdb
db = duckdb.connect("/content/mimic.duckdb")

In [ ]:
# Josh and Michael - create a shortcut to the shared "parquets" folder in your MyDrive, and the following code should work

parquet_root = "/content/drive/MyDrive/parquets/files/mimiciv/3.1/"
import glob
parquet_files = glob.glob(parquet_root + "**/*.parquet", recursive=True)
parquet_files

['/content/drive/MyDrive/parquets/files/mimiciv/3.1/hosp/admissions.parquet',
 '/content/drive/MyDrive/parquets/files/mimiciv/3.1/hosp/d_labitems.parquet',
 '/content/drive/MyDrive/parquets/files/mimiciv/3.1/hosp/d_icd_diagnoses.parquet',
 '/content/drive/MyDrive/parquets/files/mimiciv/3.1/hosp/diagnoses_icd.parquet',
 '/content/drive/MyDrive/parquets/files/mimiciv/3.1/hosp/patients.parquet',
 '/content/drive/MyDrive/parquets/files/mimiciv/3.1/hosp/labevents.parquet',
 '/content/drive/MyDrive/parquets/files/mimiciv/3.1/icu/icustays.parquet',
 '/content/drive/MyDrive/parquets/files/mimiciv/3.1/icu/chartevents.parquet']

In [ ]:
for path in parquet_files:
    table_name = (
        path.replace(parquet_root, "")
            .replace("/", "_")
            .replace(".parquet", "")
    )
    db.execute(f"CREATE VIEW IF NOT EXISTS {table_name} AS SELECT * FROM parquet_scan('{path}');")

In [ ]:
cxr_root = "/content/drive/MyDrive/parquets/files/mimic-cxr-jpg/2.1.0/"
cxr_files = glob.glob(cxr_root + "**/*.parquet", recursive=True)

for path in cxr_files:
    table_name = (
        path.replace(cxr_root, "")
            .replace("mimic-cxr-2.0.0-", "")
            .replace(".parquet", "")
    )
    db.execute(f"CREATE VIEW IF NOT EXISTS {table_name} AS SELECT * FROM parquet_scan('{path}');")
cxr_files

['/content/drive/MyDrive/parquets/files/mimic-cxr-jpg/2.1.0/mimic-cxr-2.0.0-split.parquet',
 '/content/drive/MyDrive/parquets/files/mimic-cxr-jpg/2.1.0/mimic-cxr-2.0.0-metadata.parquet',
 '/content/drive/MyDrive/parquets/files/mimic-cxr-jpg/2.1.0/mimic-cxr-2.0.0-chexpert.parquet',
 '/content/drive/MyDrive/parquets/files/mimic-cxr-jpg/2.1.0/mimic-cxr-2.0.0-negbio.parquet']

In [ ]:
db.execute("SELECT COUNT(*) FROM negbio").df()

count_star()
0        227827

In [ ]:
db.execute("SELECT COUNT(*) FROM chexpert").df()

count_star()
0        227827

In [ ]:
db.execute("SELECT COUNT(*) FROM metadata").df()

count_star()
0        377110

In [ ]:
db.execute('DESCRIBE metadata').df()

column_name column_type null   key default  \
0                                     dicom_id     VARCHAR  YES  None    None   
1                                   subject_id      BIGINT  YES  None    None   
2                                     study_id      BIGINT  YES  None    None   
3            PerformedProcedureStepDescription     VARCHAR  YES  None    None   
4                                 ViewPosition     VARCHAR  YES  None    None   
5                                         Rows      BIGINT  YES  None    None   
6                                      Columns      BIGINT  YES  None    None   
7                                    StudyDate      BIGINT  YES  None    None   
8                                    StudyTime      DOUBLE  YES  None    None   
9            ProcedureCodeSequence_CodeMeaning     VARCHAR  YES  None    None   
10                ViewCodeSequence_CodeMeaning     VARCHAR  YES  None    None   
11  PatientOrientationCodeSequence_CodeMeaning     VARCHAR  YES  None    None   

   extra  
0   None  
1   None  
2   None  
3   None  
4   None  
5   None  
6   None  
7   None  
8   None  
9   None  
10  None  
11  None

In [ ]:
db.execute("SELECT COUNT(*) FROM split").df()

count_star()
0        377110

In [ ]:
db.execute('DESCRIBE split').df()

column_name column_type null   key default extra
0    dicom_id     VARCHAR  YES  None    None  None
1    study_id      BIGINT  YES  None    None  None
2  subject_id      BIGINT  YES  None    None  None
3       split     VARCHAR  YES  None    None  None

In [ ]:
db.execute("SELECT COUNT(*) FROM hosp_patients").df()

count_star()
0        364627

In [ ]:
db.execute("SELECT COUNT(*) FROM icu_chartevents").df()

count_star()
0     432997491

In [ ]:
db.execute("""
SHOW TABLES;
""").df()

name
0               chexpert
1        hosp_admissions
2   hosp_d_icd_diagnoses
3        hosp_d_labitems
4     hosp_diagnoses_icd
5         hosp_labevents
6          hosp_patients
7        icu_chartevents
8           icu_icustays
9               metadata
10                negbio
11                 split

Replicating data processing pipeline found here: https://github.com/singlaayush/CardiomegalyBiomarkers/blob/main/Cardiomegaly_Classification/DataPipeline.ipynb

In [ ]:
# cloning cardiomegaly biomarkers repo to get access to data processing functions
!git clone https://github.com/singlaayush/CardiomegalyBiomarkers.git

Cloning into 'CardiomegalyBiomarkers'...
remote: Enumerating objects: 411, done.
remote: Counting objects: 100% (84/84), done.
remote: Compressing objects: 100% (50/50), done.
remote: Total 411 (delta 47), reused 65 (delta 32), pack-reused 327 (from 1)
Receiving objects: 100% (411/411), 5.72 MiB | 17.39 MiB/s, done.
Resolving deltas: 100% (222/222), done.


Global File Paths

In [ ]:
# Sahil and Michael - Similar to parquets shortcut, create shortcut for physionet.org folder on MyDrive
mimic_iv_path = '/content/drive/MyDrive/physionet.org/files/mimiciv/3.1/'
icu_stays_path = mimic_iv_path + 'icu/icustays.csv.gz'
chart_events_path = mimic_iv_path + 'icu/chartevents.csv.gz'
patients_table_path = mimic_iv_path + 'hosp/patients.csv.gz'
admissions_table_path = mimic_iv_path + 'hosp/admissions.csv.gz'
lab_events_path = mimic_iv_path + 'hosp/labevents.csv.gz'

mimic_cxr_path = '/content/drive/MyDrive/physionet.org/files/mimic-cxr-jpg/2.1.0/'
cxr_records_path = mimic_cxr_path + 'cxr-record-list.csv.gz'
cxr_metadata_path = mimic_cxr_path + 'mimic-cxr-2.0.0-metadata.csv.gz'
df_split_path = mimic_cxr_path + 'mimic-cxr-2.0.0-split.csv.gz'
negbio_path = mimic_cxr_path + 'mimic-cxr-2.0.0-negbio.csv.gz'
chexpert_path = mimic_cxr_path + 'mimic-cxr-2.0.0-chexpert.csv.gz'

# Features intermediate
feature_folder = '/content/drive/MyDrive/physionet.org/Mimic_features/'

# MIMIC intermediate
relevant_chart_events_save_path = feature_folder + 'RelevantChartEvents.pkl'
relevant_lab_events_save_path = feature_folder + 'RelevantLabEvents.pkl'
df_icu_xray_path =  feature_folder + 'IcuXrayMatched.pkl'

# Biomarkers
ctr_path =  '/content/drive/MyDrive/physionet.org/Biomarker_Extraction/save_folder/CTR/CTRs.csv'
cpar_path = '/content/drive/MyDrive/physionet.org/Biomarker_Extraction/save_folder/CPAR/CPARs.csv'

# Final cleaned features
features_path = feature_folder + 'MIMIC_features.pkl'


In [ ]:
db.execute('DESCRIBE hosp_patients').df()

column_name column_type null   key default extra
0         subject_id      BIGINT  YES  None    None  None
1             gender     VARCHAR  YES  None    None  None
2         anchor_age      BIGINT  YES  None    None  None
3        anchor_year      BIGINT  YES  None    None  None
4  anchor_year_group     VARCHAR  YES  None    None  None
5                dod        DATE  YES  None    None  None

Data Pipeline Functions

In [ ]:
# @title
'''  This code block contains the functions for the data pipeline, copied data_pipeline_functions.py from singlaayush github fork
'''
import sys
sys.path.append('/content/CardiomegalyBiomarkers/Cardiomegaly_Classification/src')

import datetime
import matplotlib.pyplot as plt
import numpy as np
import os
import pandas as pd
from typing import List, Dict

from utils.pandas_utils import explode, create_pivot, filter_df_isin

pd.options.mode.chained_assignment = None  # default='warn' #copy slice warning
plt.style.use('ggplot')
plt.rcParams.update({'font.size': 20})


def dfCleaning(df: pd.DataFrame) -> pd.DataFrame:
    '''Apply Mimic specific replacement functions to dataframe

    :param df: Datframe to adjust
    :type df: pd.DataFrame
    :return: Adjusted dataframe
    :rtype: pd.DataFrame
    '''

    # Map Positive and negative values to 0 for negative and 1 for positive
    df.replace({'Negative': 0, 'Positive': 1}, inplace=True)

    # Remove the .dicom from the file paths and replace with .jpg
    df['path'] = df.apply(lambda row: os.path.splitext(row['path'])[0], axis=1)
    df['path'] = df['path'].astype(str) + '.jpg'

    # Replace unrealistic CTR and CPAR values with NaN
    df.loc[df.CTR >= 1, 'CTR'] = np.nan
    df.loc[df.CPAR >= 1, 'CPAR'] = np.nan

    return df


def dfCleaningNoIDP(df: pd.DataFrame) -> pd.DataFrame:
    '''Apply Mimic specific replacement functions to dataframe

    :param df: Datframe to adjust
    :type df: pd.DataFrame
    :return: Adjusted dataframe
    :rtype: pd.DataFrame
    '''

    # Map Positive and negative values to 0 for negative and 1 for positive
    df.replace({'Negative': 0, 'Positive': 1}, inplace=True)

    # Remove the .dicom from the file paths and replace with .jpg
    df['path'] = df.apply(lambda row: os.path.splitext(row['path'])[0], axis=1)
    df['path'] = df['path'].astype(str) + '.jpg'

    # Mapping of original ethnicities to standardized categories
    ethnicity_mapping = {
        "WHITE": "White",
        "WHITE - OTHER EUROPEAN": "White",
        "WHITE - RUSSIAN": "White",
        "WHITE - EASTERN EUROPEAN": "White",
        "WHITE - BRAZILIAN": "White",
        "BLACK/AFRICAN AMERICAN": "Black",
        "BLACK/CAPE VERDEAN": "Black",
        "BLACK/CARIBBEAN ISLAND": "Black",
        "BLACK/AFRICAN": "Black",
        "ASIAN": "Asian",
        "ASIAN - CHINESE": "Asian",
        "ASIAN - SOUTH EAST ASIAN": "Asian",
        "ASIAN - ASIAN INDIAN": "Asian",
        "ASIAN - KOREAN": "Asian",
        "HISPANIC/LATINO - PUERTO RICAN": "Hispanic/Latino",
        "HISPANIC/LATINO - DOMINICAN": "Hispanic/Latino",
        "HISPANIC/LATINO - GUATEMALAN": "Hispanic/Latino",
        "HISPANIC/LATINO - SALVADORAN": "Hispanic/Latino",
        "HISPANIC OR LATINO": "Hispanic/Latino",
        "HISPANIC/LATINO - MEXICAN": "Hispanic/Latino",
        "HISPANIC/LATINO - HONDURAN": "Hispanic/Latino",
        "HISPANIC/LATINO - CUBAN": "Hispanic/Latino",
        "HISPANIC/LATINO - COLUMBIAN": "Hispanic/Latino",
        "HISPANIC/LATINO - CENTRAL AMERICAN": "Hispanic/Latino",
        "SOUTH AMERICAN": "Hispanic/Latino",
        "NATIVE HAWAIIAN OR OTHER PACIFIC ISLANDER": "Asian",
        "AMERICAN INDIAN/ALASKA NATIVE": "Other",
        "MULTIPLE RACE/ETHNICITY": "Other",
        "OTHER": "Other",
        "UNKNOWN": "Other",
        "UNABLE TO OBTAIN": "Other",
        "PATIENT DECLINED TO ANSWER": "Other",
        "PORTUGUESE": "Other"
    }

    df['ethnicity'] = df['ethnicity'].map(ethnicity_mapping)

    return df


def x_ray_dataframe_generator(
    label: str,
    view: str,
    df_cxr_records: pd.DataFrame,
    df_nb: pd.DataFrame,
    df_cx: pd.DataFrame,
    df_cxr_meta_data: pd.DataFrame,
    df_split: pd.DataFrame,
) -> pd.DataFrame:
    '''Generating a dataframe containing X-ray studies which are available in MIMIC-CXR by merging and filtering

    :param label: Disease column to keep
    :type label: str
    :param view: X-Ray view to filter for
    :type view: str
    :param df_cxr_records: Dataframe with paths for each CXR file
    :type df_cxr_records: pd.DataFrame
    :param df_nb: Dataframe with negbio labels
    :type df_nb: pd.DataFrame
    :param df_cx: Dataframe with chexpert labels
    :type df_cx: pd.DataFrame
    :param df_cxr_meta_data: Dataframe containing meta data info
    :type df_cxr_meta_data: pd.DataFrame
    :param df_split: Dataframe containing info about test and train split
    :type df_split: pd.DataFrame
    :return: Merged and filtered dataframe
    :rtype: pd.DataFrame
    '''

    # Prep cheexpert and negbio
    ## Merge chexpert with negbio
    df_cxnb = df_nb.merge(
        df_cx.drop('subject_id', axis=1),
        how='left',
        left_on='study_id',
        right_on='study_id',
        suffixes=('', '_cx'),
    )
    ## Subselect to training set
    study_ids_train = set(df_split.loc[df_split['split'] == 'train', 'study_id'])
    df_cxnb_train = df_cxnb.loc[df_cxnb['study_id'].isin(study_ids_train)]
    ## Label disagreements in label
    c_cx = f'{label}_cx'
    idx1 = df_cxnb_train[label].isnull() & df_cxnb_train[c_cx].notnull()
    idx2 = df_cxnb_train[label].notnull() & df_cxnb_train[c_cx].isnull()
    idx3 = (
        df_cxnb_train[label].notnull()
        & df_cxnb_train[c_cx].notnull()
        & (df_cxnb_train[label] != df_cxnb_train[c_cx])
    )
    df_cxnb_train.loc[(idx1 | idx2 | idx3), label] = -9
    df_cxnb_train_red = df_cxnb_train[['subject_id', 'study_id', label]]
    ## Annotate
    labels = {0: 'Negative', 1: 'Positive', -1: 'Uncertain', -9: 'Disagreement'}
    df_cxnb_train_red[label] = df_cxnb_train_red[label].map(labels)

    # Prep meta and records
    ## Merge meta with records
    df_meta_records = df_cxr_meta_data[
        [
            'dicom_id',
            'subject_id',
            'study_id',
            'StudyDate',
            'StudyTime',
            'ViewPosition',
        ]
    ].merge(
        df_cxr_records.drop(['study_id', 'subject_id'], axis=1),
        on='dicom_id',
        how='inner',
    )

    # Merge dataframes
    df_combined = df_meta_records.merge(
        df_cxnb_train_red.drop(['subject_id'], axis=1), on='study_id', how='inner'
    )

    # Filter to only include the +/- PA x-rays and for specific views
    df_combined_filtered = df_combined.loc[
        df_combined[label].isin(
            [
                'Positive',
                'Negative',
            ]
        )
    ]
    df_combined_filtered = df_combined_filtered.loc[
        df_combined_filtered['ViewPosition'] == view
    ]

    return df_combined_filtered


def x_ray_dataframe_generator_v2(
    labels: List,
    df_cxr_records: pd.DataFrame,
    df_nb: pd.DataFrame,
    df_cx: pd.DataFrame,
    df_cxr_meta_data: pd.DataFrame,
    df_split: pd.DataFrame,
    view: str = None,
) -> pd.DataFrame:
    '''Generating a dataframe containing X-ray studies which are available in \
        MIMIC-CXR by merging and filtering
    This does NOT filter the df such that it contains only Positive or \
        Negative labels to ensure multi-label support.

    :param labels: List of Disease columns to keep
    :type labels: List
    :param view: X-Ray view to filter for
    :type view: str
    :param df_cxr_records: Dataframe with paths for each CXR file
    :type df_cxr_records: pd.DataFrame
    :param df_nb: Dataframe with negbio labels
    :type df_nb: pd.DataFrame
    :param df_cx: Dataframe with chexpert labels
    :type df_cx: pd.DataFrame
    :param df_cxr_meta_data: Dataframe containing meta data info
    :type df_cxr_meta_data: pd.DataFrame
    :param df_split: Dataframe containing info about test and train split
    :type df_split: pd.DataFrame
    :return: Merged and filtered dataframe
    :rtype: pd.DataFrame
    '''
    # Prep cheexpert and negbio
    ## Merge chexpert with negbio
    df_cxnb_v2 = df_nb.merge(
        df_cx.drop('subject_id', axis=1),
        how='left',
        left_on='study_id',
        right_on='study_id',
        suffixes=('', '_cx'),
    )
    # Merge df_cxnb with df_split to add the 'split' column to df_cxnb
    df_split_unique = df_split.drop_duplicates(subset='study_id')
    df_cxnb_v2 = df_cxnb_v2.merge(
        df_split_unique[['study_id', 'split']], on='study_id', how='inner'
    )

    # Create an empty list to store filtered dataframes
    filtered_dfs = []
    for label in labels:
        c_cx = f'{label}_cx'  # CheXpert label column
        # Identify disagreement and uncertainty
        idx1 = df_cxnb_v2[label].isnull() & df_cxnb_v2[c_cx].notnull()
        idx2 = df_cxnb_v2[label].notnull() & df_cxnb_v2[c_cx].isnull()
        idx3 = (
            df_cxnb_v2[label].notnull()
            & df_cxnb_v2[c_cx].notnull()
            & (df_cxnb_v2[label] != df_cxnb_v2[c_cx])
        )
        df_cxnb_v2.loc[(idx1 | idx2 | idx3), label] = -9
        # Annotate
        labels_map = {
            0: 'Negative',
            1: 'Positive',
            -1: 'Uncertain',
            -9: 'Disagreement'
        }
        df_cxnb_v2[label] = df_cxnb_v2[label].map(labels_map)
        # Prepare filtered dataframe
        df_cxnb_train_red_v2 = df_cxnb_v2[
            ['subject_id', 'study_id', 'split', label]
        ]
        # Append filtered dataframe to the list
        filtered_dfs.append(df_cxnb_train_red_v2)

    # Prep meta and records
    ## Merge meta with records
    df_meta_records_v2 = df_cxr_meta_data[
        [
            'dicom_id',
            'subject_id',
            'study_id',
            'StudyDate',
            'StudyTime',
            'ViewPosition',
        ]
    ].merge(
        df_cxr_records.drop(['study_id', 'subject_id'], axis=1),
        on='dicom_id',
        how='inner',
    )

    filtered_df = pd.concat(filtered_dfs, axis=1).drop(['subject_id'], axis=1)
    filtered_df = filtered_df.loc[:, ~filtered_df.columns.duplicated()]

    # Merge dataframes
    df_combined_v2 = df_meta_records_v2.merge(
        filtered_df, on='study_id', how='inner'
    )

    df_combined_v2 = df_combined_v2[
        df_combined_v2.ViewPosition.isin(['AP','PA'])
    ]

    # Set other conditions to Negative if No Finding is Positive
    # Step 1: Identify the condition where 'No Finding' is 'Positive'
    condition = df_combined_v2['No Finding'] == 'Positive'
    # Step 2: Find rows that meet this condition and have any value but \
    # 'Positive' in the specified labels
    null_condition = df_combined_v2.loc[condition, labels[1:]].ne('Positive')
    # Step 3: Set these values to 'Negative'
    df_combined_v2.loc[condition, labels[1:]] = df_combined_v2.loc[condition, labels[1:]].mask(null_condition, 'Negative')

    # Remove all rows with 'Uncertain' or 'Disagreement' values from the df
    #mask = ~df_combined_v2.apply(
    #   lambda row: row.isin(['Uncertain', 'Disagreement']).any(), axis=1
    #)
    #df_combined_filtered_v2 = df_combined_v2[mask]

    return df_combined_v2


def filter_pd_read_chunkwise(
    file_path: str,
    filter_col: str,
    filter_list: List[str],
    chunksize: float,
    dtype: dict = None,
) -> pd.DataFrame:
    '''Use pd.read_csv to read csv file in chunks and filter rows where filter_col is in filter_list

    :param file_path: File path
    :type file_path: str
    :param filter_col: Column to filter by
    :type filter_col: str
    :param filter_list: Values to keep
    :type filter_list: List[str]
    :param chunksize: Chunk size
    :type chunksize: float
    :return: Filtered dataframe
    :rtype: pd.DataFrame
    '''

    chunk_csv = pd.read_csv(file_path, chunksize=chunksize, dtype=dtype)
    filtered_df = pd.concat(
        [filter_df_isin(chunk, filter_col, filter_list) for chunk in chunk_csv]
    )

    return filtered_df


def icu_xray_matcher(
    label: str,
    days_before_icu: int,
    xray_gap_after_icu: int,
    xray_max_time_after_icu: int,
    df_xray: pd.DataFrame,
    df_icu_stays: pd.DataFrame,
) -> pd.DataFrame:
    '''Linking ICU stays to X-ray studies based on their dates
    X-rays linked to ICU stays if they occurs up to 'days_before_icu' before admission, or
    between 'xray_gap_after_icu' and 'xray_max_time_after_icu' days after ICU discharge

    :param label: Disease column
    :type label: str
    :param days_before_icu: Days before icu stay to consider for xray
    :type days_before_icu: int
    :param xray_gap_after_icu: Waiting period after ICU for xrays to consider
    :type xray_gap_after_icu: int
    :param xray_max_time_after_icu: Maximum days after icu stay to consider for xray
    :type xray_max_time_after_icu: int
    :param df_xray: Dataframe with xrays
    :type df_xray: pd.DataFrame
    :param df_icu_stays: Dataframe with icu stays
    :type df_icu_stays: pd.DataFrame
    :return: Combined dataframe
    :rtype: pd.DataFrame
    '''

    # Filter for patients in icu stays with xrays
    unique_full_patients = (
        pd.merge(df_xray, df_icu_stays, on=['subject_id'], how='inner')
        .drop_duplicates(subset=['subject_id'])['subject_id']
        .reset_index(drop=True)
        .tolist()
    )
    cxrOverlap = df_xray.loc[df_xray['subject_id'].isin(unique_full_patients), :]
    icuOverlap = df_icu_stays.loc[
        df_icu_stays['subject_id'].isin(unique_full_patients), :
    ]

    # Convert objects to date times
    icuOverlap['intime'] = pd.to_datetime(icuOverlap['intime'])
    icuOverlap['outtime'] = pd.to_datetime(icuOverlap['outtime'])

    # The matching works like this:
    # First we iterate through the patients who have both ICU stays and X-ray studies.
    # For each patient we create lists for the dates, study_ids, labels, paths and view positions for all of their X-rays in MIMIC
    ICUMatcher = icuOverlap[['stay_id', 'intime', 'outtime']].copy()
    ICUMatcher['Match'] = 0
    ICUMatcher['study_id'] = 0
    ICUMatcher['Label'] = 0
    ICUMatcher['ViewPosition'] = 0
    ICUMatcher['path'] = 0
    ICUMatcher['EarlyBoundary'] = ICUMatcher['intime'] - datetime.timedelta(
        days=days_before_icu
    )
    ICUMatcher['PostGapStart'] = ICUMatcher['outtime'] + datetime.timedelta(
        days=xray_gap_after_icu
    )
    ICUMatcher['PostGapStop'] = ICUMatcher['PostGapStart'] + datetime.timedelta(
        days=xray_max_time_after_icu
    )
    # Iterate through all of the subjects
    for subid in unique_full_patients:
        PatientCXR = cxrOverlap.loc[cxrOverlap['subject_id'] == subid].reset_index(
            drop=True
        )
        PatientICU = icuOverlap.loc[icuOverlap['subject_id'] == subid].reset_index(
            drop=True
        )

        # Iterate through CXR
        CXRdates = []
        CXRstudies = []
        CXRlabels = []
        CXRpaths = []
        CXRview = []
        for (
            _,
            row,
        ) in (
            PatientCXR.iterrows()
        ):  # Populate lists with dates, times and labels of each CXR study
            date_temp = str(row['StudyDate'])
            time_temp = str(row['StudyTime']).split('.')
            if len(time_temp[0]) < 6:
                time_temp[0] = '0' * (6 - len(time_temp[0])) + time_temp[0]
            time_temp = '.'.join(time_temp)
            time_aux = 'T'.join([date_temp, time_temp])
            studytime = pd.to_datetime(time_aux)
            CXRdates.append(
                studytime
            )  # Add time for this study to the list define above
            CXRstudies.append(row['study_id'])  # Add study
            CXRlabels.append(row[label])  # Add label to label list
            CXRpaths.append(row['path'])  # Add path to list of paths
            CXRview.append(row['ViewPosition'])  # Add view position to list of views

        # Iterate through the ICU Stays
        for (
            _,
            row,
        ) in PatientICU.iterrows():  # For each of the patient's ICU stays
            ICUMatcherRow = ICUMatcher.loc[
                ICUMatcher.stay_id == row['stay_id']
            ]  # First get the stay ID
            CXRs_in_range = (
                []
            )  # Initialise an empty list which will record which of the patient's CXR's are in range of
            # this ICU stay

            for i in range(
                len(CXRdates)
            ):  # Iterate through the CXR dates and check if any fall inside the time
                # window we defined for the ICU-Stay (Daysbefore, daysafter etc)
                Date = CXRdates[i]  # First get the date of the CXR study

                # Then check if that date falls in the specified range
                if (
                    (
                        (Date > ICUMatcherRow['EarlyBoundary']).item()
                        and (Date < ICUMatcherRow['intime']).item()
                    )
                    or (
                        (Date > ICUMatcherRow['intime']).item()
                        and (Date < ICUMatcherRow['outtime']).item()
                    )
                    or (
                        (Date > ICUMatcherRow['PostGapStart']).item()
                        and (Date < ICUMatcherRow['PostGapStop']).item()
                    )
                ):

                    CXRs_in_range.append(
                        i
                    )  # If an X-ray falls in the specified window, we add it's index to the list
                    # that we initialised earlier

            # Now we know which id's from the cxr list fall in the range
            # Filter down the earlier lists so they only contain CXRs within the ICU range
            CXRdates_in_range = [
                CXRdates[i] for i in CXRs_in_range
            ]  # Just the dates of the X-rays which fell in the range
            CXRlabels_in_range = [
                CXRlabels[i] for i in CXRs_in_range
            ]  # The labels of the X-rays which fell in the range

            if len(CXRlabels_in_range) > 0:  # If at least one X-ray in the range

                # Need to find which X-ray in the range was taken closest to ICU admission.
                DaysAway = (
                    []
                )  # This list will store the distance from the ICU in-time to each X-ray study date
                # and let us pick the nearest date

                # Issues often crop up when doing this due to datatype issues but this should work.
                for x in range(len(CXRdates_in_range)):
                    TempDates = abs(
                        CXRdates_in_range[x] - ICUMatcherRow['intime']
                    )  # Get the absolute values of time between
                    # X-ray and ICU admission
                    TempDates = TempDates.dt.days  # in pandas v1; used .astype('timedelta64[D]') to convert the datatype
                    DaysAway.append(
                        TempDates.astype(int).values
                    )  # Add the value to the list

                TempIndex = DaysAway.index(
                    min(DaysAway)
                )  # Once the DaysAway list is populated we can get the index
                # of the minimum value

                ChosenDate = CXRdates_in_range[
                    TempIndex
                ]  # Using the index we can get the date from the CXRdates_in_range list
                NearestIndex = CXRdates.index(
                    ChosenDate
                )  # Using the date we can then get the index of that study in the earlier
                # CXRdates list

                # If we find a X-ray does fall window the predefined ICU time window, set flags in the matcher dataframes.
                # Then we copy the x-ray label into the ICU matcher dataframe along with the X-ray's study_id
                ICUMatcher.loc[
                    ICUMatcher.stay_id == row['stay_id'], 'Match'
                ] = 1  # set the matcher flag
                ICUMatcher.loc[
                    ICUMatcher.stay_id == row['stay_id'], 'study_id'
                ] = CXRstudies[
                    NearestIndex
                ]  # copy the study id
                # of the nearest x-ray into the ICUMatcher dataframe

                # Copy the X-ray's label, view position and path into the same dataframe
                ICUMatcher.loc[ICUMatcher.stay_id == row['stay_id'], label] = CXRlabels[
                    NearestIndex
                ]
                ICUMatcher.loc[
                    ICUMatcher.stay_id == row['stay_id'], 'ViewPosition'
                ] = CXRview[NearestIndex]
                ICUMatcher.loc[ICUMatcher.stay_id == row['stay_id'], 'path'] = CXRpaths[
                    NearestIndex
                ]

    # Getting rid of non-matches
    ICUMatcher = ICUMatcher.loc[ICUMatcher['Match'] == 1].reset_index(drop=True)
    df_combined = icuOverlap.merge(
        ICUMatcher.drop(['intime', 'outtime'], axis=1), how='right', on='stay_id'
    )

    return df_combined


def icu_xray_matcher_v2(
    labels: List,
    days_before_icu: int,
    xray_gap_after_icu: int,
    xray_max_time_after_icu: int,
    df_xray: pd.DataFrame,
    df_icu_stays: pd.DataFrame,
) -> pd.DataFrame:
    '''Linking ICU stays to X-ray studies based on their dates
    X-rays linked to ICU stays if they occurs up to 'days_before_icu' before admission, or
    between 'xray_gap_after_icu' and 'xray_max_time_after_icu' days after ICU discharge

    :param labels: list of disease columns
    :type label: List
    :param days_before_icu: Days before icu stay to consider for xray
    :type days_before_icu: int
    :param xray_gap_after_icu: Waiting period after ICU for xrays to consider
    :type xray_gap_after_icu: int
    :param xray_max_time_after_icu: Maximum days after icu stay to consider for xray
    :type xray_max_time_after_icu: int
    :param df_xray: Dataframe with xrays
    :type df_xray: pd.DataFrame
    :param df_icu_stays: Dataframe with icu stays
    :type df_icu_stays: pd.DataFrame
    :return: Combined dataframe
    :rtype: pd.DataFrame
    '''

    # Filter for patients in ICU stays with x-rays
    unique_full_patients = (
        pd.merge(df_xray, df_icu_stays, on=['subject_id'], how='inner')
        .drop_duplicates(subset=['subject_id'])['subject_id']
        .reset_index(drop=True)
        .tolist()
    )

    cxrOverlap = df_xray.loc[df_xray['subject_id'].isin(unique_full_patients), :]
    icuOverlap = df_icu_stays.loc[
        df_icu_stays['subject_id'].isin(unique_full_patients), :
    ]

    # Convert objects to datetime
    icuOverlap['intime'] = pd.to_datetime(icuOverlap['intime'])
    icuOverlap['outtime'] = pd.to_datetime(icuOverlap['outtime'])

    # Initialize the matcher dataframe
    ICUMatcher = icuOverlap[['stay_id', 'intime', 'outtime']].copy()
    ICUMatcher['Match'] = 0
    ICUMatcher['study_id'] = 0
    for label in labels:
        ICUMatcher[label] = 'Uncertain'
    ICUMatcher['ViewPosition'] = ''
    ICUMatcher['path'] = ''
    ICUMatcher['EarlyBoundary'] = ICUMatcher['intime'] - datetime.timedelta(days=days_before_icu)
    ICUMatcher['PostGapStart'] = ICUMatcher['outtime'] + datetime.timedelta(days=xray_gap_after_icu)
    ICUMatcher['PostGapStop'] = ICUMatcher['PostGapStart'] + datetime.timedelta(days=xray_max_time_after_icu)
    ICUMatcher['StudyDate'] = 0
    ICUMatcher['split'] = ''

    # Iterate through all of the subjects
    for subid in unique_full_patients:
        PatientCXR = cxrOverlap.loc[cxrOverlap['subject_id'] == subid].reset_index(drop=True)
        PatientICU = icuOverlap.loc[icuOverlap['subject_id'] == subid].reset_index(drop=True)

        # Iterate through CXR
        CXRdates = []
        CXRstudies = []
        CXRlabels = {label: [] for label in labels}
        CXRpaths = []
        CXRview = []
        CXRStudyDates = []
        CXRsplits = []

        for _, row in PatientCXR.iterrows():
            date_temp = str(row['StudyDate'])
            time_temp = str(row['StudyTime']).split('.')
            if len(time_temp[0]) < 6:
                time_temp[0] = '0' * (6 - len(time_temp[0])) + time_temp[0]
            time_temp = '.'.join(time_temp)
            time_aux = 'T'.join([date_temp, time_temp])
            studytime = pd.to_datetime(time_aux)
            CXRdates.append(studytime)
            CXRstudies.append(row['study_id'])
            for label in labels:
                CXRlabels[label].append(row[label])
            CXRpaths.append(row['path'])
            CXRview.append(row['ViewPosition'])
            CXRStudyDates.append(row['StudyDate'])
            CXRsplits.append(row['split'])

        # Iterate through the ICU Stays
        for _, row in PatientICU.iterrows():
            ICUMatcherRow = ICUMatcher.loc[ICUMatcher.stay_id == row['stay_id']]
            CXRs_in_range = []

            for i in range(len(CXRdates)):
                Date = CXRdates[i]
                if (
                    (Date > ICUMatcherRow['EarlyBoundary']).item()
                    and (Date < ICUMatcherRow['intime']).item()
                ) or (
                    (Date > ICUMatcherRow['intime']).item()
                    and (Date < ICUMatcherRow['outtime']).item()
                ) or (
                    (Date > ICUMatcherRow['PostGapStart']).item()
                    and (Date < ICUMatcherRow['PostGapStop']).item()
                ):
                    CXRs_in_range.append(i)

            if len(CXRs_in_range) > 0:
                CXRdates_in_range = [CXRdates[i] for i in CXRs_in_range]
                CXRlabels_in_range = {label: [CXRlabels[label][i] for i in CXRs_in_range] for label in labels}

                DaysAway = []
                for x in range(len(CXRdates_in_range)):
                    TempDates = abs(CXRdates_in_range[x] - ICUMatcherRow['intime'])
                    TempDates = TempDates.dt.days
                    DaysAway.append(TempDates.astype(int).values)

                TempIndex = DaysAway.index(min(DaysAway))
                ChosenDate = CXRdates_in_range[TempIndex]
                NearestIndex = CXRdates.index(ChosenDate)

                ICUMatcher.loc[ICUMatcher.stay_id == row['stay_id'], 'Match'] = 1
                ICUMatcher.loc[ICUMatcher.stay_id == row['stay_id'], 'study_id'] = CXRstudies[NearestIndex]
                for label in labels:
                    ICUMatcher.loc[ICUMatcher.stay_id == row['stay_id'], label] = CXRlabels[label][NearestIndex]
                ICUMatcher.loc[ICUMatcher.stay_id == row['stay_id'], 'ViewPosition'] = CXRview[NearestIndex]
                ICUMatcher.loc[ICUMatcher.stay_id == row['stay_id'], 'path'] = CXRpaths[NearestIndex]
                ICUMatcher.loc[ICUMatcher.stay_id == row['stay_id'], 'StudyDate'] = CXRStudyDates[NearestIndex]
                ICUMatcher.loc[ICUMatcher.stay_id == row['stay_id'], 'split'] = CXRsplits[NearestIndex]

    # Getting rid of non-matches
    ICUMatcher = ICUMatcher.loc[ICUMatcher['Match'] == 1].reset_index(drop=True)
    df_combined = icuOverlap.merge(
        ICUMatcher.drop(['intime', 'outtime'], axis=1), how='right', on='stay_id'
    )

    return df_combined


def SignalTableGeneratorNoIDP(
    df_icu_xray: pd.DataFrame,
    df_icu_timeseries: pd.DataFrame,
    df_icu_lab: pd.DataFrame,
    df_patients: pd.DataFrame,
    df_admissions: pd.DataFrame,
    chart_labels_mean: Dict[int, str],
    chart_labels_max: Dict[int, str],
    chart_labels_min: Dict[int, str],
    lab_labels_mean: Dict[int, str],
    lab_labels_max: Dict[int, str],
    lab_labels_min: Dict[int, str],
    average_by: str,
) -> pd.DataFrame:
    '''Average ICU data (vitals and labs) over a stay (or hour) and add it to the dataframe
    with the linked X-ray study together with patient and admission data, plus image-extracted
    biomarker values

    :param df_icu_xray: DataFrame to merge on
    :type df_icu_xray: pd.DataFrame
    :param df_icu_timeseries: ICU timeseries data
    :type df_icu_timeseries: pd.DataFrame
    :param df_icu_lab: Lab timeseries data
    :type df_icu_lab: pd.DataFrame
    :param df_patients: Patient info data
    :type df_patients: pd.DataFrame
    :param df_admissions: Admission data
    :type df_admissions: pd.DataFrame
    :param df_ctr: CTR values
    :type df_ctr: pd.DataFrame
    :param df_cpar: CPAR values
    :type df_cpar: pd.DataFrame
    :param chart_labels_mean: Labels
    :type chart_labels_mean: Dict[int, str]
    :param chart_labels_max: Labels
    :type chart_labels_max: Dict[int, str]
    :param chart_labels_min: Labels
    :type chart_labels_min: Dict[int, str]
    :param lab_labels_mean: Labels
    :type lab_labels_mean: Dict[int, str]
    :param lab_labels_max: Labels
    :type lab_labels_max: Dict[int, str]
    :param lab_labels_min: Labels
    :type lab_labels_min: Dict[int, str]
    :param average_by: Average bu Hourly or Stay
    :type average_by: str
    :return: Combined dataframe
    :rtype: pd.DataFrame:
    '''

    # Prep df_icu_xray dataframe
    df_icu_xray = df_icu_xray.drop_duplicates(subset=['path'])
    df_icu_xray['intime'] = pd.to_datetime(df_icu_xray['intime'])
    df_icu_xray['outtime'] = pd.to_datetime(df_icu_xray['outtime'])

    # Merge the patient info and admission table
    df_patient_admission = (
        df_admissions[['subject_id', 'ethnicity']]
        .drop_duplicates(subset=['subject_id'])
        .merge(
            df_patients[['subject_id', 'anchor_age', 'anchor_year', 'gender']].drop_duplicates(
                subset=['subject_id']
            ),
            on='subject_id',
            how='left',
        )
    )

    # Merge df_patient_admission onto df_icu_xray based on subject_id
    df_icu_xray_patient_admission = df_icu_xray.merge(
        df_patient_admission, how='left', on='subject_id'
    )

    # Compare year intime to anchor_year to find approximate admission age --> kept in 'anchor_age' column to avoid future conflicts
    df_icu_xray_patient_admission['anchor_age'] = df_icu_xray_patient_admission['anchor_age'] + df_icu_xray_patient_admission['intime'].dt.year - df_icu_xray_patient_admission['anchor_year']

    df_icu_xray_patient_admission.drop(['anchor_year'],axis=1)


    # Prep timeseries tables

    if average_by == 'Hourly':
        df_icu_xray_patient_admission = explode_icu_stays(df_icu_xray_patient_admission)

    ## Adjust timestamps
    if average_by == 'Hourly':
        df_icu_timeseries['charttime'] = pd.to_datetime(df_icu_timeseries['charttime'])
        df_icu_lab['charttime'] = pd.to_datetime(df_icu_lab['charttime'])
        df_icu_timeseries['charttime'] = df_icu_timeseries['charttime'].dt.round(
            '60min'
        )
        df_icu_lab['charttime'] = df_icu_lab['charttime'].dt.round('60min')

    ## Get matchers
    if average_by == 'Hourly':
        ChartUniqueMatcher = ['subject_id', 'charttime']
        LabUniqueMatcher = ['subject_id', 'charttime']
    elif average_by == 'Stay':
        ChartUniqueMatcher = 'stay_id'
        LabUniqueMatcher = 'hadm_id'

    ## Create pivot tables from timeseries table for various aggregation levels and merge together
    df_icu_timeseries_pivoted = create_pivot(
        df=df_icu_timeseries,
        labels=chart_labels_mean,
        labels_column='itemid',
        unique_matcher=ChartUniqueMatcher,
        aggfunc='mean',
        values='valuenum',
    )
    pivot_aux = create_pivot(
        df=df_icu_timeseries,
        labels=chart_labels_max,
        labels_column='itemid',
        unique_matcher=ChartUniqueMatcher,
        aggfunc='max',
        values='valuenum',
    )
    df_icu_timeseries_pivoted = df_icu_timeseries_pivoted.merge(
        pivot_aux, how='outer', on=ChartUniqueMatcher
    )
    pivot_aux = create_pivot(
        df=df_icu_timeseries,
        labels=chart_labels_min,
        labels_column='itemid',
        unique_matcher=ChartUniqueMatcher,
        aggfunc='min',
        values='valuenum',
    )
    df_icu_timeseries_pivoted = df_icu_timeseries_pivoted.merge(
        pivot_aux, how='outer', on=ChartUniqueMatcher
    )
    df_icu_lab_pivoted = create_pivot(
        df=df_icu_lab,
        labels=lab_labels_mean,
        labels_column='itemid',
        unique_matcher=LabUniqueMatcher,
        aggfunc='mean',
        values='valuenum',
    )
    pivot_aux = create_pivot(
        df=df_icu_lab,
        labels=lab_labels_max,
        labels_column='itemid',
        unique_matcher=LabUniqueMatcher,
        aggfunc='max',
        values='valuenum',
    )
    df_icu_lab_pivoted = df_icu_lab_pivoted.merge(
        pivot_aux, how='outer', on=LabUniqueMatcher
    )
    pivot_aux = create_pivot(
        df=df_icu_lab,
        labels=lab_labels_min,
        labels_column='itemid',
        unique_matcher=LabUniqueMatcher,
        aggfunc='min',
        values='valuenum',
    )
    df_icu_lab_pivoted = df_icu_lab_pivoted.merge(
        pivot_aux, how='outer', on=LabUniqueMatcher
    )

    # Merge the timeseries pivot tables onto the df_icu_xray_patient_admission table
    df_icu_xray_patient_admission_timeseries = df_icu_xray_patient_admission.merge(
        df_icu_timeseries_pivoted, how='left', on=ChartUniqueMatcher
    )
    df_icu_xray_patient_admission_timeseries_lab = (
        df_icu_xray_patient_admission_timeseries.merge(
            df_icu_lab_pivoted, how='left', on=LabUniqueMatcher
        )
    )

    # return final output
    return df_icu_xray_patient_admission_timeseries_lab


def SignalTableGenerator(
    df_icu_xray: pd.DataFrame,
    df_icu_timeseries: pd.DataFrame,
    df_icu_lab: pd.DataFrame,
    df_patients: pd.DataFrame,
    df_admissions: pd.DataFrame,
    df_ctr: pd.DataFrame,
    df_cpar: pd.DataFrame,
    chart_labels_mean: Dict[int, str],
    chart_labels_max: Dict[int, str],
    chart_labels_min: Dict[int, str],
    lab_labels_mean: Dict[int, str],
    lab_labels_max: Dict[int, str],
    lab_labels_min: Dict[int, str],
    average_by: str,
) -> pd.DataFrame:
    '''Average ICU data (vitals and labs) over a stay (or hour) and add it to the dataframe
    with the linked X-ray study together with patient and admission data, plus image-extracted
    biomarker values

    :param df_icu_xray: DataFrame to merge on
    :type df_icu_xray: pd.DataFrame
    :param df_icu_timeseries: ICU timeseries data
    :type df_icu_timeseries: pd.DataFrame
    :param df_icu_lab: Lab timeseries data
    :type df_icu_lab: pd.DataFrame
    :param df_patients: Patient info data
    :type df_patients: pd.DataFrame
    :param df_admissions: Admission data
    :type df_admissions: pd.DataFrame
    :param df_ctr: CTR values
    :type df_ctr: pd.DataFrame
    :param df_cpar: CPAR values
    :type df_cpar: pd.DataFrame
    :param chart_labels_mean: Labels
    :type chart_labels_mean: Dict[int, str]
    :param chart_labels_max: Labels
    :type chart_labels_max: Dict[int, str]
    :param chart_labels_min: Labels
    :type chart_labels_min: Dict[int, str]
    :param lab_labels_mean: Labels
    :type lab_labels_mean: Dict[int, str]
    :param lab_labels_max: Labels
    :type lab_labels_max: Dict[int, str]
    :param lab_labels_min: Labels
    :type lab_labels_min: Dict[int, str]
    :param average_by: Average bu Hourly or Stay
    :type average_by: str
    :return: Combined dataframe
    :rtype: pd.DataFrame:
    '''

    # Prep df_icu_xray dataframe
    df_icu_xray = df_icu_xray.drop_duplicates(subset=['path'])
    df_icu_xray['intime'] = pd.to_datetime(df_icu_xray['intime'])
    df_icu_xray['outtime'] = pd.to_datetime(df_icu_xray['outtime'])

    # Merge the patient info and admission table
    df_patient_admission = (
        df_admissions[['subject_id', 'ethnicity']]
        .drop_duplicates(subset=['subject_id'])
        .merge(
            df_patients[['subject_id', 'anchor_age', 'anchor_year', 'gender']].drop_duplicates(
                subset=['subject_id']
            ),
            on='subject_id',
            how='left',
        )
    )

    # Merge df_patient_admission onto df_icu_xray based on subject_id
    df_icu_xray_patient_admission = df_icu_xray.merge(
        df_patient_admission, how='left', on='subject_id'
    )

    # Compare year intime to anchor_year to find approximate admission age --> kept in 'anchor_age' column to avoid future conflicts
    df_icu_xray_patient_admission['anchor_age'] = df_icu_xray_patient_admission['anchor_age'] + df_icu_xray_patient_admission['intime'].dt.year - df_icu_xray_patient_admission['anchor_year']

    df_icu_xray_patient_admission.drop(['anchor_year'],axis=1)


    # Prep timeseries tables

    if average_by == 'Hourly':
        df_icu_xray_patient_admission = explode_icu_stays(df_icu_xray_patient_admission)

    ## Adjust timestamps
    if average_by == 'Hourly':
        df_icu_timeseries['charttime'] = pd.to_datetime(df_icu_timeseries['charttime'])
        df_icu_lab['charttime'] = pd.to_datetime(df_icu_lab['charttime'])
        df_icu_timeseries['charttime'] = df_icu_timeseries['charttime'].dt.round(
            '60min'
        )
        df_icu_lab['charttime'] = df_icu_lab['charttime'].dt.round('60min')

    ## Get matchers
    if average_by == 'Hourly':
        ChartUniqueMatcher = ['subject_id', 'charttime']
        LabUniqueMatcher = ['subject_id', 'charttime']
    elif average_by == 'Stay':
        ChartUniqueMatcher = 'stay_id'
        LabUniqueMatcher = 'hadm_id'

    ## Create pivot tables from timeseries table for various aggregation levels and merge together
    df_icu_timeseries_pivoted = create_pivot(
        df=df_icu_timeseries,
        labels=chart_labels_mean,
        labels_column='itemid',
        unique_matcher=ChartUniqueMatcher,
        aggfunc='mean',
        values='valuenum',
    )
    pivot_aux = create_pivot(
        df=df_icu_timeseries,
        labels=chart_labels_max,
        labels_column='itemid',
        unique_matcher=ChartUniqueMatcher,
        aggfunc='max',
        values='valuenum',
    )
    df_icu_timeseries_pivoted = df_icu_timeseries_pivoted.merge(
        pivot_aux, how='outer', on=ChartUniqueMatcher
    )
    pivot_aux = create_pivot(
        df=df_icu_timeseries,
        labels=chart_labels_min,
        labels_column='itemid',
        unique_matcher=ChartUniqueMatcher,
        aggfunc='min',
        values='valuenum',
    )
    df_icu_timeseries_pivoted = df_icu_timeseries_pivoted.merge(
        pivot_aux, how='outer', on=ChartUniqueMatcher
    )
    df_icu_lab_pivoted = create_pivot(
        df=df_icu_lab,
        labels=lab_labels_mean,
        labels_column='itemid',
        unique_matcher=LabUniqueMatcher,
        aggfunc='mean',
        values='valuenum',
    )
    pivot_aux = create_pivot(
        df=df_icu_lab,
        labels=lab_labels_max,
        labels_column='itemid',
        unique_matcher=LabUniqueMatcher,
        aggfunc='max',
        values='valuenum',
    )
    df_icu_lab_pivoted = df_icu_lab_pivoted.merge(
        pivot_aux, how='outer', on=LabUniqueMatcher
    )
    pivot_aux = create_pivot(
        df=df_icu_lab,
        labels=lab_labels_min,
        labels_column='itemid',
        unique_matcher=LabUniqueMatcher,
        aggfunc='min',
        values='valuenum',
    )
    df_icu_lab_pivoted = df_icu_lab_pivoted.merge(
        pivot_aux, how='outer', on=LabUniqueMatcher
    )

    # Merge the timeseries pivot tables onto the df_icu_xray_patient_admission table
    df_icu_xray_patient_admission_timeseries = df_icu_xray_patient_admission.merge(
        df_icu_timeseries_pivoted, how='left', on=ChartUniqueMatcher
    )
    df_icu_xray_patient_admission_timeseries_lab = (
        df_icu_xray_patient_admission_timeseries.merge(
            df_icu_lab_pivoted, how='left', on=LabUniqueMatcher
        )
    )

    # Merge CTR and CPAR dataframes onto df_icu_xray_patient_admission_timeseries_lab table
    df_icu_xray_patient_admission_timeseries_lab['dicom_file'] = pd.Series(df_icu_xray_patient_admission_timeseries_lab.path.str[-48:-4])

    df_icu_xray_patient_admission_timeseries_lab_ctr = df_icu_xray_patient_admission_timeseries_lab.merge(df_ctr, on = 'dicom_file')
    df_icu_xray_patient_admission_timeseries_lab_ctr_cpar = df_icu_xray_patient_admission_timeseries_lab_ctr.merge(df_cpar, on = 'dicom_file')

    df_icu_xray_patient_admission_timeseries_lab_ctr_cpar.drop(labels='dicom_file', axis=1, inplace=True)

    # return final output
    return df_icu_xray_patient_admission_timeseries_lab_ctr_cpar


def explode_icu_stays(df: pd.DataFrame) -> pd.DataFrame:
    '''Create a new column 'charttime' in df
    For each row in df:
    Get intime and outime of that ICU stay
    Create a list of date-times in hourly increments between intime and outime
    (For example if someone was in the ICU on 05/12/2020 from 2pm till 5pm, create the list [2020-12-05 14:00:000,
    2020-12-05 15:00:000, 2020-12-05 16:00:000,])
    Insert this list into the 'charttime' column

    After inserting this list into every row of df, we then explode the dataframe based on the charttime column
    Each value in the charttime list for that row will now get its own row.

    All of the values in the new row (i.e. subject id, patient age, study id...) will be the same as in the original row
    except that the charttime will be different for each row

    The example above would produce 3 rows, each with a different charttime but all the other
    values (id, age, ethnicity, etc) would be the same

    :param df: Dataframe to explode
    :type df: pd.DataFrame
    :return: Exploded dataframe
    :rtype: pd.DataFrame
    '''

    # insert charttime column
    df.insert(
        1, 'charttime', np.nan
    )  # Chart time will be the actual date and time, and is
    # used for matching chart events
    df['charttime'] = df['charttime'].astype('object')  # set type as object

    # Also include a Time column which will be an integer for each hour
    df.insert(1, 'Time', np.nan)  # i.e. 1 for hour 1, 2 for the second hour, 3...
    df['Time'] = df['Time'].astype('object')

    # Round intime and outime to the hour, (everything so far has already been rounded to the hour)
    df['intime'] = df['intime'].dt.round('60min')
    df['outtime'] = df['outtime'].dt.round('60min')

    # Iterate through rows in df
    for i, _ in df.iterrows():  # for each row
        datelist = pd.date_range(
            start=df.loc[i, 'intime'],
            end=df.loc[i, 'outtime'],
            freq='60min',
        ).tolist()
        # create the list of datetimes in hourly increments

        timelist = list(range(len(datelist)))  # also create the list of integers
        df.at[i, 'charttime'] = datelist  # insert charttime lists into the row
        df.at[i, 'Time'] = timelist  # also insert the integer time list into the row

    df_exploded = explode(
        df, lst_cols=['charttime', 'Time']
    )  # Explode the dataframe using the times,
    # so that each row now represents an hour but still has the same patient information (age, gender) as when
    # each row represented an entire stay

    return df_exploded

In [ ]:
from tqdm import tqdm

def filter_pd_read_chunkwise_v2(
    file_path: str,
    filter_col: str,
    filter_list: List[str],
    chunksize: float,
    dtype: dict = None,
) -> pd.DataFrame:

    chunk_iter = pd.read_csv(file_path, chunksize=chunksize, dtype=dtype)

    filtered_chunks = []

    # Wrap the iterator in tqdm for a progress bar
    for chunk in tqdm(chunk_iter, desc="Reading CSV in chunks"):
        filtered_chunks.append(filter_df_isin(chunk, filter_col, filter_list))

    return pd.concat(filtered_chunks)

Parameters

In [ ]:
# General Parameters
label = 'Cardiomegaly'  # Define label of target disease ('Atelectasis', 'Cardiomegaly', 'Consolidation', 'Edema', 'Enlarged Cardiomediastinum', 'Fracture', 'Lung Lesion', 'Lung Opacity', 'No Finding', 'Pleural Effusion', 'Pleural Other', 'Pneumonia', 'Pneumothorax', 'Support Devices')
chunk_size = 10**7     # When extracting relevant lab and chart events we iterate through the original files in chunks of size 'chunk_size'.

# MIMIC-CXR (imaging) Parameters
view = 'PA'     # Choose the X-ray view position you're interested in, AP or PA

# MIMIC-IV (non-imaging) Parameters
MIMIC_IV_version = 3            # Version of MIMIC-IV downloaded
days_before_icu = 365           # The number of days before ICU admission that we look for x-rays in
xray_gap_after_icu = 0          # You can choose to include a 'gap' after ICU discharge in which you don't look for any X-rays
xray_max_time_after_icu = 90    # If you don't want a gap, xray_max_time_after_icu is just the number of days after ICU discharge that we look for x-rays in. We look for x-rays which are between Gap and Gap + xray_max_time_after_icu days after out-time
average_by = 'Stay'             # 'Hourly' to average readings every hour and have one hour per row; 'Stay', to average chart and lab values across a stay
filter_col = 'itemid'   	    # Define features to use for time-series prep

In [ ]:
# @title
# Labels of desired non-imaging features

# Labels
chart_labels_mean = {
    220045: 'HR_mean',
    220277: 'SpO2_mean',
    223761: 'Temp(F)_mean',
    220210: 'RR_mean',
    220052: 'ABPm_mean',
    220051: 'ABPd_mean',
    220050: 'ABPs_mean',
    220180: 'NBPd_mean',
    220181: 'NBPm_mean',
    220179: 'NBPs_mean',
    223835: 'FiO2_mean',
    220274: 'PH_mean',
    220235: 'PCO2_mean',
    220227: 'SaO2_mean',
    227457: 'PlateletCount_mean',
    227456: 'Albumin_mean',
    220603: 'Cholesterol_mean',
    220645: 'Sodium_mean',
    220224: 'PO2_mean',
}

chart_labels_max = {
    220045: 'HR_max',
    220210: 'RR_max',
    220052: 'ABPm_max',
    220051: 'ABPd_max',
    220050: 'ABPs_max',
    220180: 'NBPd_max',
    220181: 'NBPm_max',
    220179: 'NBPs_max',
    223835: 'FiO2_max',
    220235: 'PCO2_max',
    220645: 'Sodium_max',
}

chart_labels_min = {
    220045: 'HR_min',
    220277: 'SpO2_min',
    220210: 'RR_min',
    220052: 'ABPm_min',
    220051: 'ABPd_min',
    220050: 'ABPs_min',
    220180: 'NBPd_min',
    220181: 'NBPm_min',
    220179: 'NBPs_min',
    220235: 'PCO2_min',
    220645: 'Sodium_min',
}

lab_labels_mean = {
    50826: 'Tidal_Volume_mean',
    51006: 'Urea_Nitrogren_mean',
    50863: 'Alkaline_Phosphatase_mean',
    50893: 'Calcium_Total_mean',
    50902: 'Chloride_mean',
    50931: 'Glucose_mean',
    50813: 'Lactate_mean',
    50960: 'Magnesium_mean',
    50970: 'Phosphate_mean',
    50971: 'Potassium_mean',
    50885: 'Bilirubin',
    51003: 'Troponin-T_mean',
    51221: 'Hematocrit_mean',
    50811: 'Hemoglobin_mean',
    50861: 'ALT_mean',
    50912: 'Creatinine_mean',
    51275: 'PTT_mean',
    51516: 'WBC_mean',
    51214: 'Fibrinogen',
}

lab_labels_max = {
    50971: 'Potassium_max',
    51003: 'Troponin-T_max',
    50811: 'Hemoglobin_max',
    51516: 'WBC_max',
}

lab_labels_min = {
    50971: 'Potassium_min',
    50811: 'Hemoglobin_min',
    51516: 'WBC_min',
}

# Aggregation of all laboratory items into LabItems
LabItems = dict(lab_labels_mean)
LabItems.update(lab_labels_max)
LabItems.update(lab_labels_min)

# Aggregation of the vital signs / chart items into ChartItems
ChartItems = dict(chart_labels_mean)
ChartItems.update(chart_labels_max)
ChartItems.update(chart_labels_min)

Getting MIMIC-IV Data

In [ ]:
from CardiomegalyBiomarkers.Cardiomegaly_Classification.src.data_pipeline_functions import filter_pd_read_chunkwise
# MIMIC-IV: Extract necessary features chunkwise
# This will process 44 chunks, doesn't run successfully due to System RAM limit
df_icu_timeseries = filter_pd_read_chunkwise(
    file_path=chart_events_path,
    filter_col=filter_col,
    filter_list=ChartItems.keys(),
    chunksize=chunk_size,
)


In [ ]:
# This will process 16 chunks, doesn't run successfully due to System Ram limit
# Only functional difference in v2 function is showing progress bar?
df_icu_lab = filter_pd_read_chunkwise_v2(
    file_path=lab_events_path,
    filter_col=filter_col,
    filter_list=LabItems.keys(),
    chunksize=chunk_size,
)


Reading CSV in chunks: 16it [03:53, 14.60s/it]


In [ ]:
df_icu_timeseries.to_pickle(relevant_chart_events_save_path)

In [ ]:
df_icu_lab.to_pickle(relevant_lab_events_save_path)

Match MIMIC-IV and MIMIC-CXR Data

In [ ]:
# This cell takes ~10 minutes to run
df_split = pd.read_csv(df_split_path)
df_metadata = pd.read_csv(cxr_metadata_path, header=0, sep=',')
df_cxr_records = pd.read_csv(cxr_records_path, header=0, sep=',')
df_nb = pd.read_csv(negbio_path)
df_cx = pd.read_csv(chexpert_path)

# MIMIC-CXR: Create X-Ray dataframes (the table will only contain the paths to the actual pictures)
labels = [
    'No Finding',
    'Enlarged Cardiomediastinum',
    'Cardiomegaly',
    'Lung Opacity',
    'Lung Lesion',
    'Edema',
    'Consolidation',
    'Pneumonia',
    'Atelectasis',
    'Pneumothorax',
    'Pleural Effusion',
    'Pleural Other',
    'Fracture',
    'Support Devices']


df_xray_v2 = x_ray_dataframe_generator_v2(
    # TEST: just use cardiomegaly label like OG does
    labels=labels,
    df_cxr_records=df_cxr_records,
    df_nb=df_nb,
    df_cx=df_cx,
    df_cxr_meta_data=df_metadata,
    df_split=df_split)
# Link X-Ray to ICU stays if in certain time window defined by days_before_icu, xray_gap_after_icu, and xray_max_time_after_icu
df_icu_stays = pd.read_csv(icu_stays_path)

df_icu_xray_v2 = icu_xray_matcher_v2(
    labels=labels,
    days_before_icu=days_before_icu,
    xray_gap_after_icu=xray_gap_after_icu,
    xray_max_time_after_icu=xray_max_time_after_icu,
    df_xray=df_xray_v2,
    df_icu_stays=df_icu_stays)
df_icu_xray_v2.to_pickle(df_icu_xray_path)

Creating master cleaned dataframe

In [ ]:
# Load data
df_patients = pd.read_csv(patients_table_path)
df_admissions = pd.read_csv(admissions_table_path)
df_icu_xray = pd.read_pickle(df_icu_xray_path)

df_icu_lab = pd.read_pickle(relevant_lab_events_save_path)
df_icu_timeseries = pd.read_pickle(relevant_chart_events_save_path)
# edit name of df_admissions column if data taken from versions after MIMIC-IV v1.0 as 'ethnicity' column was renamed 'race' in following version (v2.0)
if MIMIC_IV_version != 1:
    df_admissions.rename(columns={'race':'ethnicity'}, inplace=True)
# collate all features (MIMIC-IV feautres, MIMIC-CXR file paths, biomarker values) into one master table
df_master = SignalTableGeneratorNoIDP(df_icu_xray,
                                 df_icu_timeseries=df_icu_timeseries,
                                 df_icu_lab=df_icu_lab,
                                 df_patients=df_patients,
                                 df_admissions=df_admissions,
                                 chart_labels_mean=chart_labels_mean,
                                 chart_labels_max=chart_labels_max,
                                 chart_labels_min=chart_labels_min,
                                 lab_labels_mean=lab_labels_mean,
                                 lab_labels_max=lab_labels_max,
                                 lab_labels_min=lab_labels_min,
                                 average_by=average_by)
# Clean master table
df_master_cleaned = dfCleaningNoIDP(df_master)
# Save cleaned master dataframe
df_master_cleaned.to_pickle(feature_folder + 'MIMIC_features_v3.pkl')
df_master_cleaned.shape

(22982, 102)

In [ ]:
df_master =  pd.read_pickle(feature_folder + 'MIMIC_features_v3.pkl')

In [ ]:
list(df_master.columns.values)

['subject_id',
 'hadm_id',
 'stay_id',
 'first_careunit',
 'last_careunit',
 'intime',
 'outtime',
 'los',
 'Match',
 'study_id',
 'No Finding',
 'Enlarged Cardiomediastinum',
 'Cardiomegaly',
 'Lung Opacity',
 'Lung Lesion',
 'Edema',
 'Consolidation',
 'Pneumonia',
 'Atelectasis',
 'Pneumothorax',
 'Pleural Effusion',
 'Pleural Other',
 'Fracture',
 'Support Devices',
 'ViewPosition',
 'path',
 'EarlyBoundary',
 'PostGapStart',
 'PostGapStop',
 'StudyDate',
 'split',
 'ethnicity',
 'anchor_age',
 'anchor_year',
 'gender',
 'HR_mean',
 'ABPs_mean',
 'ABPd_mean',
 'ABPm_mean',
 'NBPs_mean',
 'NBPd_mean',
 'NBPm_mean',
 'RR_mean',
 'PO2_mean',
 'SaO2_mean',
 'PCO2_mean',
 'PH_mean',
 'SpO2_mean',
 'Cholesterol_mean',
 'Sodium_mean',
 'Temp(F)_mean',
 'FiO2_mean',
 'Albumin_mean',
 'PlateletCount_mean',
 'HR_max',
 'ABPs_max',
 'ABPd_max',
 'ABPm_max',
 'NBPs_max',
 'NBPd_max',
 'NBPm_max',
 'RR_max',
 'PCO2_max',
 'Sodium_max',
 'FiO2_max',
 'HR_min',
 'ABPs_min',
 'ABPd_min',
 'ABPm_mi

In [ ]:
import pandas as pd
df_master_idp = pd.read_pickle('/content/CardiomegalyBiomarkers/Cardiomegaly_Classification/MIMIC_features_OG/MIMIC_features.pkl')

In [ ]:
print(df_master_idp['path'][1])

files/p10/p10002013/s52163036/1e647043-eed3576e-3123c170-780cb897-93a89502.jpg


In [ ]:
df_master_idp.shape


(2662, 90)

In [ ]:
pd.set_option('display.max_columns', None)
df_sorted_ibp = df_master_idp.sort_values(by='subject_id', ascending=True)
df_sorted_ibp.head()


subject_id   hadm_id   stay_id  \
0    10001884  26184834  37510196   
1    10002013  23581541  39060235   
2    10004457  23251352  31494479   
3    10011365  26712576  37153661   
4    10012292  28665904  37005236   

                                 first_careunit  \
0            Medical Intensive Care Unit (MICU)   
1  Cardiac Vascular Intensive Care Unit (CVICU)   
2  Cardiac Vascular Intensive Care Unit (CVICU)   
3  Cardiac Vascular Intensive Care Unit (CVICU)   
4            Medical Intensive Care Unit (MICU)   

                                  last_careunit              intime  \
0            Medical Intensive Care Unit (MICU) 2131-01-11 04:20:05   
1  Cardiac Vascular Intensive Care Unit (CVICU) 2160-05-18 10:00:53   
2  Cardiac Vascular Intensive Care Unit (CVICU) 2141-12-17 10:24:25   
3  Cardiac Vascular Intensive Care Unit (CVICU) 2166-02-11 16:03:00   
4            Medical Intensive Care Unit (MICU) 2171-07-17 20:39:42   

              outtime       los  Match  study_id  Label ViewPosition  \
0 2131-01-20 08:27:30  9.171817      1  55333410      0           PA   
1 2160-05-19 17:33:33  1.314352      1  52163036      0           PA   
2 2141-12-18 14:16:17  1.161019      1  55439624      0           PA   
3 2166-02-20 08:54:53  8.702697      1  56594284      0           PA   
4 2171-07-21 04:46:45  3.338229      1  52412975      0           PA   

                                                path       EarlyBoundary  \
0  files/p10/p10001884/s55333410/5b135035-4708084... 2130-01-11 04:20:05   
1  files/p10/p10002013/s52163036/1e647043-eed3576... 2159-05-19 10:00:53   
2  files/p10/p10004457/s55439624/ad41d9ed-37ff140... 2140-12-17 10:24:25   
3  files/p10/p10011365/s56594284/ff295ca5-9f888b5... 2165-02-11 16:03:00   
4  files/p10/p10012292/s52412975/ca16ea39-8c22bfd... 2170-07-17 20:39:42   

         PostGapStart         PostGapStop  Cardiomegaly  \
0 2131-01-20 08:27:30 2131-04-20 08:27:30             1   
1 2160-05-19 17:33:33 2160-08-17 17:33:33             1   
2 2141-12-18 14:16:17 2142-03-18 14:16:17             0   
3 2166-02-20 08:54:53 2166-05-21 08:54:53             0   
4 2171-07-21 04:46:45 2171-10-19 04:46:45             1   

                ethnicity  anchor_age  anchor_year gender    HR_mean  \
0  BLACK/AFRICAN AMERICAN          77         2122      F  70.800000   
1                   WHITE          57         2156      F  94.214286   
2                   WHITE          66         2140      M  94.967742   
3                   WHITE          82         2157      F  87.030837   
4                   WHITE          72         2168      F  97.731707   

    ABPs_mean  ABPd_mean  ABPm_mean   NBPs_mean  NBPd_mean  NBPm_mean  \
0         NaN        NaN        NaN  129.176471  74.669683  90.529412   
1  110.619048  61.476190  76.700000  110.500000  64.500000  75.400000   
2  109.038462  57.346154  73.076923  103.181818  52.363636  63.909091   
3         NaN        NaN        NaN  128.018605  56.953271  73.483568   
4         NaN        NaN        NaN  127.411765  71.602941  84.632353   

     RR_mean    PO2_mean  SaO2_mean  PCO2_mean   PH_mean  SpO2_mean  \
0  19.044444   75.000000  91.000000  54.000000  7.355000  97.648649   
1  15.185185  282.875000  97.333333  45.000000       NaN  96.730769   
2  15.031250  324.285714  96.500000  38.142857  7.430000  98.312500   
3  21.704846  108.000000  98.000000  33.250000  7.421429  92.409692   
4  23.195122  198.000000  99.000000  52.000000       NaN  93.012195   

   Cholesterol_mean  Sodium_mean  Temp(F)_mean  FiO2_mean  Albumin_mean  \
0               NaN   136.500000     98.989130  45.000000         3.075   
1               NaN   138.333333     97.500000  66.666667           NaN   
2               NaN   139.000000     98.000000  70.000000           NaN   
3               NaN   140.266667     99.589091  46.415094         2.300   
4               NaN   143.333333     98.005556  63.260870           NaN   

   PlateletCount_mean  HR_max  ABPs_max  ABPd_max  

In [ ]:
pd.set_option('display.max_columns', None)
df_sorted = df_master.sort_values(by='subject_id', ascending=True)
df_sorted.head()

subject_id   hadm_id   stay_id                       first_careunit  \
0    10000032  29079034  39553978   Medical Intensive Care Unit (MICU)   
1    10000980  26913865  39765666   Medical Intensive Care Unit (MICU)   
3    10001217  27703517  34592300  Surgical Intensive Care Unit (SICU)   
2    10001217  24597018  37067082  Surgical Intensive Care Unit (SICU)   
4    10001884  26184834  37510196   Medical Intensive Care Unit (MICU)   

                         last_careunit              intime  \
0   Medical Intensive Care Unit (MICU) 2180-07-23 14:00:00   
1   Medical Intensive Care Unit (MICU) 2189-06-27 08:42:00   
3  Surgical Intensive Care Unit (SICU) 2157-12-19 15:42:24   
2  Surgical Intensive Care Unit (SICU) 2157-11-20 19:18:02   
4   Medical Intensive Care Unit (MICU) 2131-01-11 04:20:05   

              outtime       los  Match  study_id No Finding  \
0 2180-07-23 23:50:47  0.410266      1  53911762          1   
1 2189-06-27 20:38:27  0.497535      1  51967283        NaN   
3 2157-12-20 14:27:41  0.948113      1  58913004        NaN   
2 2157-11-21 22:08:00  1.118032      1  52067803        NaN   
4 2131-01-20 08:27:30  9.171817      1  57156853        NaN   

  Enlarged Cardiomediastinum  Cardiomegaly Lung Opacity Lung Lesion Edema  \
0                          0             0            0           0     0   
1                        NaN           NaN          NaN           1   NaN   
3                        NaN  Disagreement          NaN         NaN   NaN   
2                        NaN           NaN          NaN         NaN   NaN   
4                        NaN           NaN          NaN         NaN     1   

  Consolidation Pneumonia Atelectasis  Pneumothorax Pleural Effusion  \
0             0         0           0             0                0   
1           NaN         1         NaN           NaN              NaN   
3           NaN       NaN         NaN  Disagreement              NaN   
2           NaN       NaN           1           NaN              NaN   
4           NaN       NaN         NaN           NaN              NaN   

  Pleural Other Fracture Support Devices ViewPosition  \
0             0        0               0           AP   
1           NaN      NaN             NaN           AP   
3           NaN      NaN    Disagreement           AP   
2           NaN      NaN             NaN           PA   
4           NaN      NaN             NaN           AP   

                                                path       EarlyBoundary  \
0  files/p10/p10000032/s53911762/68b5c4b1-227d048... 2179-07-24 14:00:00   
1  files/p10/p10000980/s51967283/943486a3-b3fa9ff... 2188-06-27 08:42:00   
3  files/p10/p10001217/s58913004/5e54fc9c-37c4983... 2156-12-19 15:42:24   
2  files/p10/p10001217/s52067803/a917c883-720a5bb... 2156-11-20 19:18:02   
4  files/p10/p10001884/s57156853/9fd47edd-0708720... 2130-01-11 04:20:05   

         PostGapStart         PostGapStop  StudyDate  split ethnicity  \
0 2180-07-23 23:50:47 2180-10-21 23:50:47   21800723  train     White   
1 2189-06-27 20:38:27 2189-09-25 20:38:27   21890627  train     Black   
3 2157-12-20 14:27:41 2158-03-20 14:27:41   21571218  train     White   
2 2157-11-21 22:08:00 2158-02-19 22:08:00   21571118  train     White   
4 2131-01-20 08:27:30 2131-04-20 08:27:30   21310110  train     Black   

   anchor_age  anchor_year gender    HR_mean  ABPs_mean  ABPd_mean  ABPm_mean  \
0          52         2180      F  96.500000        NaN        NaN        NaN   
1          76         2186      F  73.636364        NaN        NaN        NaN   
3          55         2157      F  79.600000        NaN        NaN        NaN   
2          55         2157      F  93.296296        NaN        NaN        NaN   
4          77         2122      F  70.800000        NaN        NaN        NaN   

    NBPs_mean  NBPd_mean  NBPm_mean    RR_mean  PO2_mean  SaO2_mean  \
0   88.900000  54.100000  62.300000  20.700000       NaN        NaN   
1  142.454545  83.272727  97.545455  20.54

In [ ]:
list(df_master_idp.columns.values)

['subject_id',
 'hadm_id',
 'stay_id',
 'first_careunit',
 'last_careunit',
 'intime',
 'outtime',
 'los',
 'Match',
 'study_id',
 'Label',
 'ViewPosition',
 'path',
 'EarlyBoundary',
 'PostGapStart',
 'PostGapStop',
 'Cardiomegaly',
 'ethnicity',
 'anchor_age',
 'anchor_year',
 'gender',
 'HR_mean',
 'ABPs_mean',
 'ABPd_mean',
 'ABPm_mean',
 'NBPs_mean',
 'NBPd_mean',
 'NBPm_mean',
 'RR_mean',
 'PO2_mean',
 'SaO2_mean',
 'PCO2_mean',
 'PH_mean',
 'SpO2_mean',
 'Cholesterol_mean',
 'Sodium_mean',
 'Temp(F)_mean',
 'FiO2_mean',
 'Albumin_mean',
 'PlateletCount_mean',
 'HR_max',
 'ABPs_max',
 'ABPd_max',
 'ABPm_max',
 'NBPs_max',
 'NBPd_max',
 'NBPm_max',
 'RR_max',
 'PCO2_max',
 'Sodium_max',
 'FiO2_max',
 'HR_min',
 'ABPs_min',
 'ABPd_min',
 'ABPm_min',
 'NBPs_min',
 'NBPd_min',
 'NBPm_min',
 'RR_min',
 'PCO2_min',
 'SpO2_min',
 'Sodium_min',
 'Hemoglobin_mean',
 'Lactate_mean',
 'Tidal_Volume_mean',
 'ALT_mean',
 'Alkaline_Phosphatase_mean',
 'Bilirubin',
 'Calcium_Total_mean',
 'Chlo

# START BELOW FOR BARTTENDER EXPERIMENTS

In [ ]:
# Setup env
from google.colab import drive
drive.mount('/content/drive')
!git clone https://github.com/singlaayush/barttender.git
!git clone https://github.com/singlaayush/CardiomegalyBiomarkers.git

Mounted at /content/drive
Cloning into 'barttender'...
remote: Enumerating objects: 144, done.
remote: Counting objects: 100% (144/144), done.
remote: Compressing objects: 100% (95/95), done.
remote: Total 144 (delta 67), reused 122 (delta 45), pack-reused 0 (from 0)
Receiving objects: 100% (144/144), 7.04 MiB | 39.40 MiB/s, done.
Resolving deltas: 100% (67/67), done.
Cloning into 'CardiomegalyBiomarkers'...
remote: Enumerating objects: 411, done.
remote: Counting objects: 100% (84/84), done.
remote: Compressing objects: 100% (50/50), done.
remote: Total 411 (delta 47), reused 65 (delta 32), pack-reused 327 (from 1)
Receiving objects: 100% (411/411), 5.72 MiB | 33.48 MiB/s, done.
Resolving deltas: 100% (222/222), done.


In [ ]:
# Install necessary imports
!pip install pytorch_lightning --quiet
!pip install tqdm statsmodels --quiet
!pip install fire plt --quiet

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 849.5/849.5 kB 30.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 983.2/983.2 kB 61.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.9/115.9 kB 7.3 MB/s eta 0:00:00


#### Barttender constants (mimic_constants.py with updated paths)

In [ ]:
# Write over original constants file
%%writefile /content/barttender/mimic_constants.py

# @title
# mimic_constants.py - unchanged except for paths
import pandas as pd
from pathlib import Path
import os
import re
import glob
import torch
import numpy as np
import pandas as pd
import torch.nn as nn
import pytorch_lightning as pl
import torch.nn.functional as F
import torchvision.models as models
from sklearn.model_selection import train_test_split
from pathlib import Path

num_classes = 1

## THESE PATHS NEED TO BE UPDATED
# every path returned from this file MUST be a pathlib.Path object
# Updated paths for user environment
home_out_dir = Path('/content/drive/MyDrive/physionet.org/outputs/cardiomegaly')
scratch_dir  = Path('/content/drive/MyDrive/physionet.org/files/mimic-cxr-jpg/2.1.0')  # MIMIC-CXR-JPG images
nb_group_dir = Path('/content/drive/MyDrive/physionet.org/files/mimic-cxr-jpg/2.1.0/preprocessed')  # Preprocessed images directory

# Import cleaned master dataframe
feature_folder = Path('/content/drive/MyDrive/physionet.org/Mimic_features/')

def get_master_df(idp=False):
    if idp:
        # (2662, 104)
        return pd.read_pickle('/content/CardiomegalyBiomarkers/Cardiomegaly_Classification/MIMIC_features_OG/MIMIC_features.pkl')
    return pd.read_pickle('/content/drive/MyDrive/physionet.org/Mimic_features/MIMIC_features_v3.pkl')

def get_cardiomegaly_df(idp=False):
    df = None
    if idp:
        df = pd.read_pickle('/content/CardiomegalyBiomarkers/Cardiomegaly_Classification/MIMIC_features_OG/MIMIC_features.pkl')
    else:
        df = pd.read_pickle('/content/drive/MyDrive/physionet.org/Mimic_features/MIMIC_features_v3.pkl')
    return df[df['Cardiomegaly'].isin([0, 1])]

def df_train_test_split(df, test_size=0.2, val_size=0.1):
    # Pre-select test samples
    test_set = df[df['split'] == 'test']

    # Remaining data (not in the test set)
    remaining_df = df[df['split'] != 'test']

    # Group remaining data by 'subject_id'
    grouped = remaining_df.groupby('subject_id')

    # Ensure each subject is fully in one of the splits
    subjects = grouped.first().index

    # Determine split sizes
    total_remaining = len(remaining_df)
    num_test = len(test_set)
    adjusted_test_size = round(test_size - (num_test / len(df)), 2)
    adjusted_train_size = round(1 - adjusted_test_size - val_size, 2)

    # Perform stratified train/val/test split based on subject_id
    train_subjects, val_test_subjects = train_test_split(subjects,
                                                         test_size=round(val_size + adjusted_test_size, 2),
                                                         train_size=adjusted_train_size,
                                                         random_state=42)

    val_subjects, new_test_subjects = train_test_split(val_test_subjects,
                                                       test_size=round(adjusted_test_size / (val_size + adjusted_test_size), 2),
                                                       train_size=round(val_size / (val_size + adjusted_test_size), 2),
                                                       random_state=42)

    # Build the final splits
    train_set = remaining_df[remaining_df['subject_id'].isin(train_subjects)]
    val_set = remaining_df[remaining_df['subject_id'].isin(val_subjects)]
    new_test_set = remaining_df[remaining_df['subject_id'].isin(new_test_subjects)]

    # Combine pre-selected test set with the newly created test set
    final_test_set = pd.concat([test_set, new_test_set])

    # Add the split labels to the sets
    train_set.loc[:, 'split'] = 'train'
    val_set.loc[:, 'split'] = 'val'
    final_test_set.loc[:, 'split'] = 'test'

    return train_set.reset_index(drop=True), val_set.reset_index(drop=True), final_test_set.reset_index(drop=True)

# includes those with a high number of NaNs
significant_variables_all = ['age_val', 'RR_mean', 'Chloride_mean', 'Urea_Nitrogren_mean', 'SaO2_mean', \
    'PTT_mean', 'Magnesium_mean', 'PO2_mean', 'PCO2_mean', 'Lactate_mean', 'Phosphate_mean', 'Glucose_mean', 'FiO2_mean', 'PH_mean']

# includes only those with a small number of NaNs
significant_variables = ['age_val', 'Chloride_mean', 'RR_mean', 'Urea_Nitrogren_mean', 'Magnesium_mean', 'Glucose_mean', 'Phosphate_mean', 'Hematocrit_mean']

# Run if testing ablations
significant_variables = ['NBPd_mean', 'Temp(F)_mean', 'NBPm_mean', 'Sodium_mean',
       'PlateletCount_mean', 'RR_mean', 'HR_mean', 'SpO2_mean',
       'Hematocrit_mean', 'Chloride_mean', 'Urea_Nitrogren_mean',
       'Glucose_mean']

lr_variables_all = [
    'Temp(F)_mean',
    'Sodium_mean',
    'PlateletCount_mean',
    'HR_mean',
    'NBPm_mean',
    'NBPs_mean',
    'RR_mean',
    'SpO2_mean',
    'NBPd_mean',
    'Glucose_mean',
    'Creatinine_mean',
    'Chloride_mean',
    'Magnesium_mean',
    'PTT_mean',
    'Calcium_Total_mean',
    'Phosphate_mean',
    'Urea_Nitrogren_mean',
    'Hematocrit_mean',
    'Potassium_mean'
]

significant_variables_areas = {
    'image': slice(None, 185),
	'age_bar': slice(185, 188),
	'chloride_bar': slice(188, 193),
	'rr_bar': slice(193, 198),
	'urea_nitrogen_bar': slice(198, 203),
	'magnesium_bar': slice(203, 209),
	'glucose_bar': slice(209, 214),
	'phosphate_bar': slice(214, 219),
	'hematocrit_bar': slice(219, None)
}

def get_significant_variables_areas(image_type):
    return {
        f'{image_type}': slice(None, 185),
	    'age_bar': slice(185, 188),
	    'chloride_bar': slice(188, 193),
	    'rr_bar': slice(193, 198),
	    'urea_nitrogen_bar': slice(198, 203),
	    'magnesium_bar': slice(203, 209),
	    'glucose_bar': slice(209, 214),
	    'phosphate_bar': slice(214, 219),
	    'hematocrit_bar': slice(219, None)
    }

z_scores = {
    "Cardiomegaly": {
        'age': 15.3406,
        'urea_nitrogen': -11.3091,
        'chloride': 11.1641,
        'rr': 6.8814,
        'magnesium': 5.1887,
        'glucose': -3.7193,
        'phosphate': 3.3469,
        'hematocrit': -3.2741
    }
}

# Labels
chart_labels_mean = {
    220045: 'HR_mean',
    220277: 'SpO2_mean',
    223761: 'Temp(F)_mean',
    220210: 'RR_mean',
    220052: 'ABPm_mean',
    220051: 'ABPd_mean',
    220050: 'ABPs_mean',
    220180: 'NBPd_mean',
    220181: 'NBPm_mean',
    220179: 'NBPs_mean',
    223835: 'FiO2_mean',
    220274: 'PH_mean',
    220235: 'PCO2_mean',
    220227: 'SaO2_mean',
    227457: 'PlateletCount_mean',
    227456: 'Albumin_mean',
    220603: 'Cholesterol_mean',
    220645: 'Sodium_mean',
    220224: 'PO2_mean',
}

chart_labels_max = {
    220045: 'HR_max',
    220210: 'RR_max',
    220052: 'ABPm_max',
    220051: 'ABPd_max',
    220050: 'ABPs_max',
    220180: 'NBPd_max',
    220181: 'NBPm_max',
    220179: 'NBPs_max',
    223835: 'FiO2_max',
    220235: 'PCO2_max',
    220645: 'Sodium_max',
}

chart_labels_min = {
    220045: 'HR_min',
    220277: 'SpO2_min',
    220210: 'RR_min',
    220052: 'ABPm_min',
    220051: 'ABPd_min',
    220050: 'ABPs_min',
    220180: 'NBPd_min',
    220181: 'NBPm_min',
    220179: 'NBPs_min',
    220235: 'PCO2_min',
    220645: 'Sodium_min',
}

lab_labels_mean = {
    50826: 'Tidal_Volume_mean',
    51006: 'Urea_Nitrogren_mean',
    50863: 'Alkaline_Phosphatase_mean',
    50893: 'Calcium_Total_mean',
    50902: 'Chloride_mean',
    50931: 'Glucose_mean',
    50813: 'Lactate_mean',
    50960: 'Magnesium_mean',
    50970: 'Phosphate_mean',
    50971: 'Potassium_mean',
    50885: 'Bilirubin',
    51003: 'Troponin-T_mean',
    51221: 'Hematocrit_mean',
    50811: 'Hemoglobin_mean',
    50861: 'ALT_mean',
    50912: 'Creatinine_mean',
    51275: 'PTT_mean',
    51516: 'WBC_mean',
    51214: 'Fibrinogen',
}

lab_labels_max = {
    50971: 'Potassium_max',
    51003: 'Troponin-T_max',
    50811: 'Hemoglobin_max',
    51516: 'WBC_max',
}

lab_labels_min = {
    50971: 'Potassium_min',
    50811: 'Hemoglobin_min',
    51516: 'WBC_min',
}

# Aggregation of all laboratory items into LabItems
LabItems = dict(lab_labels_mean)
LabItems.update(lab_labels_max)
LabItems.update(lab_labels_min)

# Aggregation of the vital signs / chart items into ChartItems
ChartItems = dict(chart_labels_mean)
ChartItems.update(chart_labels_max)
ChartItems.update(chart_labels_min)

indexing_cols = ['subject_id', 'study_id']
imaging_cols  = ['ViewPosition', 'path']
icu_cols = ['hadm_id', 'stay_id', 'first_careunit', 'last_careunit', 'intime', 'outtime', 'los', 'Match',\
    'EarlyBoundary', 'PostGapStart', 'PostGapStop']
label_cols = ['No Finding', 'Enlarged Cardiomediastinum', 'Cardiomegaly', 'Lung Opacity', 'Lung Lesion', \
    'Edema', 'Consolidation', 'Pneumonia', 'Atelectasis', 'Pneumothorax', 'Pleural Effusion', 'Pleural Other',\
    'Fracture', 'Support Devices']
demographic_cols = ['ethnicity', 'anchor_age', 'anchor_year', 'gender']
chart_labels_mean_cols = list(chart_labels_mean.values())
chart_labels_max_cols  = list(chart_labels_max.values())
chart_labels_min_cols  = list(chart_labels_min.values())
lab_labels_mean_cols   = list(lab_labels_mean.values())
lab_labels_max_cols    = list(lab_labels_max.values())
lab_labels_min_cols    = list(lab_labels_min.values())

stats_header = ['filename', 'area', 'mean', 'min', '25th_percentile', 'median',
               '75th_percentile', 'max', 'std_mean', 'std_median']

stats_header_debug = ['filename', 'area', 'mean', 'min', '25th_percentile', 'median',
               '75th_percentile', 'max', 'std_mean', 'std_median', 'mean_w_frac', 'mean_w_iou', 'fraction_attn_area', 'iou']

k_fold_run_id = {'xray' : 'wqzq428c',
'noise': 'jfpf2s6m',
'blank': 'yxa5wmrg'}

def rgb2gray(rgb):
    return np.dot(rgb[...,:3], [0.2989, 0.5870, 0.1140])

def get_barcode_order_info(order=None, no_bars=False, nan=False, only_bars=False, bar_variables=significant_variables):
    if no_bars:
        return None, 'no_bars'
    if nan:
        bar_variables=significant_variables_all
    if only_bars:
        bar_variables=lr_variables_all
    og_order = np.array(bar_variables)
    order = [int(x) for x in order.strip('[]').split(',')] if isinstance(order, str) else order
    order = list(range(len(bar_variables))) if order is None else order
    suffix = '_'.join(og_order[order]).replace('_mean', '').replace('_val', '').lower()
    return order, suffix

def get_preproc_subpath(image_type, suffix):
    return Path(f'preproc_224x224_{image_type}_{suffix}')

def get_mask_save_dir_path(image_type, suffix, mask_type, label):
    return nb_group_dir / f'{image_type}_{suffix}/{mask_type}/{mask_type}_{label.lower().replace(" ", "_")}_maps/'

def get_mask_stats_csv_path(image_type, suffix, mask_type, label):
    return nb_group_dir / f'{image_type}_{suffix}/{mask_type}/{mask_type}_{label.lower().replace(" ", "_")}_stats.csv'

def get_mask_stats_csv(image_type, suffix, mask_type, label):
    return pd.read_csv(get_mask_stats_csv_path(image_type, suffix, mask_type, label), names=stats_header_debug)

def sanity_check_stats_csv(stats_df, areas=significant_variables_areas):
    total_len = stats_df.shape[0]
    for key in areas.keys():
        len_non_zero = stats_df[(stats_df['area'] == key) & (stats_df['mean'] > 0)].shape[0]
        print(f"For {key}: {len_non_zero} samples out of {total_len} are non-zero.")

def get_correct_root_dir(sub_path):
    if (scratch_dir / sub_path).exists():
        return scratch_dir
    if (nb_group_dir / sub_path).exists():
        return nb_group_dir
    return ''

def construct_preproc_path(og_path: str, root_dir: Path, preproc_dir=None):
    split = og_path.split("/")
    preproc_filename = f"{split[2]}_{split[3]}_{split[4]}"
    if preproc_dir:
        return root_dir / preproc_dir / preproc_filename
    else:
        return root_dir / preproc_filename

def construct_preproc_path_str(og_path: str, root_dir: Path, preproc_dir=None):
    return construct_preproc_path(og_path, root_dir, preproc_dir).as_posix()

def df_add_preproc_path_col(df, data_dir, preproc_dir):
    df['path_preproc'] = df['path'].apply(construct_preproc_path_str, args=(data_dir, preproc_dir))
    return df

def get_merged_stats_sample_df(image_type, suffix, mask_type, label, split, idp):
    df = get_master_df(idp)
    stats_df = get_mask_stats_csv(image_type, suffix, mask_type, label)
    preproc_dir = get_preproc_subpath(image_type, suffix)
    root_dir = get_correct_root_dir(preproc_dir)
    df = df_add_preproc_path_col(df, root_dir, preproc_dir)
    df['path_mask'] = df['path_preproc'].apply(lambda path_preproc: (get_mask_save_dir_path(image_type, suffix, mask_type, label) / os.path.basename(path_preproc).replace('.jpg', '.npy')).as_posix())
    merged_df = stats_df.merge(df.rename(columns={'path_mask': 'filename'}), how='left', on='filename')
    return merged_df

def get_newest_wandb_run_id(img_type_order):
    # Pattern to match directories
    pattern = re.compile(rf'densenet-{re.escape(img_type_order)}-(.+)')

    # List to store matching directories with their modification times
    directories = []

    # Iterate over all directories in the base path
    for entry in os.scandir(home_out_dir):
        if entry.is_dir():
            match = pattern.match(entry.name)
            if match:
                # Append directory name and modification time
                directories.append((entry.name, entry.stat().st_mtime))

    if not directories:
        return None, None

    # Sort directories by modification time (newest first)
    directories.sort(key=lambda x: x[1], reverse=True)

    # Get the newest directory
    newest_dir = directories[0][0]

    # Extract the run id from the directory name
    run_id = pattern.match(newest_dir).group(1)

    return run_id

def get_checkpoint_path(image_type: str, suffix: str, run_id: str = None):
    wandb_run_id = run_id if run_id else get_newest_wandb_run_id(f'{image_type}-{suffix}')
    checkpoint_files = list((home_out_dir / f"mimic/{wandb_run_id}/checkpoints/").glob("*.ckpt"))
    if not checkpoint_files:
        raise FileNotFoundError(f"No trained checkpoint found for wandb run id {wandb_run_id}")
    # If there are multiple checkpoints, select the checkpoint with the latest step
    checkpoint_file = sorted(checkpoint_files, key=lambda x: int(x.as_posix().split('step=')[1].split('.ckpt')[0]))[-1]
    return checkpoint_file  # type: Path

class DenseNet(pl.LightningModule):
    def __init__(self, num_classes):
        super().__init__()
        self.num_classes = num_classes
        self.model = models.densenet121()
        num_features = self.model.classifier.in_features
        self.model.classifier = nn.Linear(num_features, self.num_classes)

    def remove_head(self):
        num_features = self.model.classifier.in_features
        id_layer = nn.Identity(num_features)
        self.model.classifier = id_layer

    def forward(self, x):
        return self.model.forward(x)

    def configure_optimizers(self):
        params_to_update = []
        for param in self.parameters():
            if param.requires_grad == True:
                params_to_update.append(param)
        optimizer = torch.optim.Adam(params_to_update, lr=0.001)
        return optimizer

    def unpack_batch(self, batch):
        return batch['image'], batch['label']

    def process_batch(self, batch):
        img, lab = self.unpack_batch(batch)
        out = self.forward(img)
        prob = torch.sigmoid(out)
        loss = F.binary_cross_entropy(prob, lab)
        return loss

    def training_step(self, batch, batch_idx):
        loss = self.process_batch(batch)
        self.log('train_loss', loss)
        return loss

    def validation_step(self, batch, batch_idx):
        loss = self.process_batch(batch)
        self.log('val_loss', loss)

    def test_step(self, batch, batch_idx):
        loss = self.process_batch(batch)
        self.log('test_loss', loss)

def standardize_mimic_ethnicity(df):
    # Mapping of original ethnicities to standardized categories
    ethnicity_mapping = {
        "WHITE": "White",
        "WHITE - OTHER EUROPEAN": "White",
        "WHITE - RUSSIAN": "White",
        "WHITE - EASTERN EUROPEAN": "White",
        "WHITE - BRAZILIAN": "White",
        "BLACK/AFRICAN AMERICAN": "Black",
        "BLACK/CAPE VERDEAN": "Black",
        "BLACK/CARIBBEAN ISLAND": "Black",
        "BLACK/AFRICAN": "Black",
        "ASIAN": "Asian",
        "ASIAN - CHINESE": "Asian",
        "ASIAN - SOUTH EAST ASIAN": "Asian",
        "ASIAN - ASIAN INDIAN": "Asian",
        "ASIAN - KOREAN": "Asian",
        "HISPANIC/LATINO - PUERTO RICAN": "Hispanic/Latino",
        "HISPANIC/LATINO - DOMINICAN": "Hispanic/Latino",
        "HISPANIC/LATINO - GUATEMALAN": "Hispanic/Latino",
        "HISPANIC/LATINO - SALVADORAN": "Hispanic/Latino",
        "HISPANIC OR LATINO": "Hispanic/Latino",
        "HISPANIC/LATINO - MEXICAN": "Hispanic/Latino",
        "HISPANIC/LATINO - HONDURAN": "Hispanic/Latino",
        "HISPANIC/LATINO - CUBAN": "Hispanic/Latino",
        "HISPANIC/LATINO - COLUMBIAN": "Hispanic/Latino",
        "HISPANIC/LATINO - CENTRAL AMERICAN": "Hispanic/Latino",
        "SOUTH AMERICAN": "Hispanic/Latino",
        "NATIVE HAWAIIAN OR OTHER PACIFIC ISLANDER": "Asian",
        "AMERICAN INDIAN/ALASKA NATIVE": "Other",
        "MULTIPLE RACE/ETHNICITY": "Other",
        "OTHER": "Other",
        "UNKNOWN": "Other",
        "UNABLE TO OBTAIN": "Other",
        "PATIENT DECLINED TO ANSWER": "Other",
        "PORTUGUESE": "Other"
    }

    df['ethnicity'] = df['ethnicity'].map(ethnicity_mapping)

    return df

Overwriting /content/barttender/mimic_constants.py


In [ ]:
# Overwrite mimic_constants_ptit as well with general purpose constants file
!cp /content/barttender/mimic_constants.py /content/barttender/mimic_constants_ptit.py

#### Define funcs for preparing baseline data according to Barttender repo scripts (logistic regression) and Cardiomegaly repo scripts (XGBoost)

In [ ]:
# @title
#!/usr/bin/env python3
"""
Functions for baseline comparisons (Logistic Regression, XGBoost) for Barttender
"""

import sys
sys.path.append('/content/barttender/')

import sys
from pathlib import Path
from mimic_constants import *
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split, KFold
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler
from xgboost import XGBClassifier  # Using actual XGBoost from CardiomegalyBiomarkers/XGBoost.ipynb
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score, f1_score, confusion_matrix, matthews_corrcoef, average_precision_score
import statsmodels.api as sm


def prepare_data(remove_high_nan=True, nan_threshold=1000, tabular_only=False, idp_only=False):

    # Prepare data for baseline models (shallow ML on tabular/scalar features).

    # Filter df to Cardiomegaly samples only
    # We are ONLY using the idp df, which is what Barttender did for baseline (with and without the two IDP columns), so the tables are comparable
    label = 'Cardiomegaly'
    df = get_cardiomegaly_df(idp=True)

    print(f"Total samples: {len(df)}")

    # Calculate age
    if 'StudyDate' in df.columns and 'anchor_year' in df.columns:
        study_year = np.floor(df['StudyDate'] / 10000)
        delta_years = study_year - df['anchor_year']
        df['age'] = df['anchor_age'] + delta_years
    else:
        df['age'] = df['anchor_age']

    # Normalize age (0-100 to 0-1)
    df['age_label'] = df['anchor_age'].apply(lambda x: min(x / 100, 1))
    demographic_cols = ['age_label']  # idpOnly age, no race/sex (matching limited notebook)

    # Encode demographics - this could be an ablation if we want to hardcode demo info into the features
    # df = standardize_mimic_ethnicity(df)
    #
    # if 'ethnicity' in df.columns:
    #     df['race_label'] = df['ethnicity']
    #     # Handle both standardized and non-standardized ethnicity values
    #     df.loc[df['race_label'] == 'White', 'race_label'] = 0
    #     df.loc[df['race_label'] == 'Asian', 'race_label'] = 1
    #     df.loc[df['race_label'] == 'Black', 'race_label'] = 2
    #     df.loc[df['race_label'] == 'Hispanic/Latino', 'race_label'] = 3
    #     df.loc[df['race_label'] == 'Other', 'race_label'] = 4
    #     # Handle any remaining string values (convert to numeric or drop)
    #     # If race_label is still string after mapping, it means it's an unexpected value
    #     if df['race_label'].dtype == 'object':
    #         # Convert any remaining non-numeric values to 'Other' (4)
    #         mask = pd.to_numeric(df['race_label'], errors='coerce').isna()
    #         df.loc[mask, 'race_label'] = 4
    #     df['race_label'] = pd.to_numeric(df['race_label'], errors='coerce')
    #
    # if 'gender' in df.columns:
    #     df['sex_label'] = df['gender']
    #     df.loc[df['sex_label'] == 'M', 'sex_label'] = 0
    #     df.loc[df['sex_label'] == 'F', 'sex_label'] = 1
    #
    # demographic_cols = ['age_label', 'race_label', 'sex_label']

    # Prepare features based on mode
    # First, only 8 significant tabular features (matching mimic-lr-idp-limited.ipynb)
    feature_cols = demographic_cols + [v for v in significant_variables[1:] if v in df.columns]

    # Add idp features
    idp_features = ['CTR', 'CPAR']
    if not tabular_only:
        for feat in idp_features:
            if feat in df.columns and feat not in feature_cols:
                feature_cols.append(feat)

    # If idp_only, only use these two features
    if idp_only:
        feature_cols = idp_features

    # Prepare splits
    if tabular_only:
        # For limited features (matching paper), use standard 80/20 split (matching mimic-lr-idp-limited.ipynb)
        # Don't use the 'split' column - create our own split
        X = df[feature_cols]
        Y = df[[label]]  # Keep as DataFrame for stratify
        X_train, X_test, Y_train, Y_test = train_test_split(
            X, Y, test_size=0.2, random_state=42, stratify=Y[label]
        )
        Y_train = Y_train[label].astype(float)
        Y_test = Y_test[label].astype(float)
    elif 'split' in df.columns:
        # For non-limited mode, use split column if available
        X_train = df[df['split'] == 'train'][feature_cols]
        Y_train = df[df['split'] == 'train'][label].astype(float)
        X_test = df[df['split'] == 'test'][feature_cols]
        Y_test = df[df['split'] == 'test'][label].astype(float)

        # Adjust Train-Test Split to 90/10 (matching notebook Cell 43) - only for no-IDP dataset
        if tabular_only:
            # Calculate the number of samples to move from train to test
            additional_test_samples = 916

            # Sampling additional samples from X_train and Y_train
            X_train_to_test, X_train = train_test_split(
                X_train,
                test_size=(len(X_train) - additional_test_samples) / len(X_train),
                random_state=42,
                stratify=Y_train
            )
            Y_train_to_test, Y_train = train_test_split(
                Y_train,
                test_size=(len(Y_train) - additional_test_samples) / len(Y_train),
                random_state=42,
                stratify=Y_train
            )

            # Concatenate the sampled data to the test sets
            X_test = pd.concat([X_test, X_train_to_test], axis=0)
            Y_test = pd.concat([Y_test, Y_train_to_test], axis=0)
    else:
        # If no split column, create train/test split
        X = df[feature_cols]
        Y = df[label].astype(float)
        X_train, X_test, Y_train, Y_test = train_test_split(
            X, Y, test_size=0.2, random_state=42, stratify=Y
        )

    print(f"Train samples: {len(X_train)}, Test samples: {len(X_test)}")

    return X_train, X_test, Y_train, Y_test, feature_cols

def compute_metrics(y_true, y_pred, y_prob):
    """
    Compute various classification metrics for binary classification.
    Based on: barttender/notebooks/mimic-lr-idp-limited.ipynb
    """
    auc = roc_auc_score(y_true, y_prob)
    avg_precision = average_precision_score(y_true, y_prob)

    # Convert y_pred to binary predictions if it's probabilities
    y_pred_binary = (y_pred > 0.5).astype(int) if len(y_pred.shape) == 1 or y_pred.shape[1] == 1 else (y_pred > 0.5).astype(int)

    # Compute confusion matrix
    cm = confusion_matrix(y_true, y_pred_binary)

    # Metrics calculations
    tpr = cm[1, 1] / (cm[1, 1] + cm[1, 0]) if (cm[1, 1] + cm[1, 0]) > 0 else 0  # Sensitivity, Recall
    tnr = cm[0, 0] / (cm[0, 0] + cm[0, 1]) if (cm[0, 0] + cm[0, 1]) > 0 else 0  # Specificity
    ppv = cm[1, 1] / (cm[1, 1] + cm[0, 1]) if (cm[1, 1] + cm[0, 1]) > 0 else 0  # Precision
    npv = cm[0, 0] / (cm[0, 0] + cm[1, 0]) if (cm[0, 0] + cm[1, 0]) > 0 else 0  # Negative Predictive Value
    f1 = f1_score(y_true, y_pred_binary)
    mcc = matthews_corrcoef(y_true, y_pred_binary)

    return {
        'AUC': auc,
        'Average Precision': avg_precision,
        'TPR': tpr,
        'TNR': tnr,
        'PPV': ppv,
        'NPV': npv,
        'F1': f1,
        'MCC': mcc
    }

def run_logistic_regression(X_train, X_test, Y_train, Y_test, n_splits=10):
    """
    Run logistic regression baseline.

    Based on: barttender/notebooks/mimic-lr-no-idp.ipynb (Cells 24-29)
    Uses statsmodels.Logit for logistic regression with feature importance (Z-scores).
    """


    # 10-fold cross-validation approach (matching paper methodology)
    # Based on: barttender/notebooks/mimic-lr-idp-limited.ipynb
    # The notebook does: 80/20 split for test, then 10-fold CV on the 80%
    # For each fold, evaluate on the SAME held-out test set
    # So we use X_train/Y_train for CV, and X_test/Y_test as the held-out test set

    # Initialize 10-fold cross-validation on training data
    kf = KFold(n_splits=n_splits, shuffle=True, random_state=42)

    # Initialize lists to store results
    fold_metrics = []
    fold_coefficients = []
    best_fold, best_mcc, best_z_scores = (0, 0, None)

    for fold, (train_index, val_index) in enumerate(kf.split(X_train), 1):
        X_train_fold = X_train.iloc[train_index]
        X_val_fold = X_train.iloc[val_index]
        Y_train_fold = Y_train.iloc[train_index] if hasattr(Y_train, 'iloc') else Y_train[train_index]
        Y_val_fold = Y_train.iloc[val_index] if hasattr(Y_train, 'iloc') else Y_train[val_index]

        # Mean Imputation for NaNs
        imputer = SimpleImputer(strategy='mean')
        X_train_imputed = pd.DataFrame(
            imputer.fit_transform(X_train_fold),
            columns=X_train_fold.columns
        )
        X_val_imputed = pd.DataFrame(
            imputer.transform(X_val_fold),
            columns=X_val_fold.columns
        )
        # Use the SAME test set for all folds (matching notebook)
        X_test_imputed = pd.DataFrame(
            imputer.transform(X_test),
            columns=X_test.columns
        )

        # One-hot encode race_label if present
        if 'race_label' in X_train_imputed.columns:
            X_train_encoded = pd.get_dummies(
                X_train_imputed,
                columns=['race_label'],
                drop_first=True,
                dtype=float
            )
            X_val_encoded = pd.get_dummies(
                X_val_imputed,
                columns=['race_label'],
                drop_first=True,
                dtype=float
            )
            X_test_encoded = pd.get_dummies(
                X_test_imputed,
                columns=['race_label'],
                drop_first=True,
                dtype=float
            )
            # Ensure same columns
            X_val_encoded = X_val_encoded.reindex(
                columns=X_train_encoded.columns,
                fill_value=0
            )
            X_test_encoded = X_test_encoded.reindex(
                columns=X_train_encoded.columns,
                fill_value=0
            )
        else:
            X_train_encoded = X_train_imputed
            X_val_encoded = X_val_imputed
            X_test_encoded = X_test_imputed

        # Add constant term
        X_train_encoded = sm.add_constant(X_train_encoded)
        X_val_encoded = sm.add_constant(X_val_encoded)
        X_test_encoded = sm.add_constant(X_test_encoded)

        # Reset indices
        X_train_encoded = X_train_encoded.reset_index(drop=True)
        if hasattr(Y_train_fold, 'reset_index'):
            Y_train_fold = Y_train_fold.reset_index(drop=True)
        X_val_encoded = X_val_encoded.reset_index(drop=True)
        if hasattr(Y_val_fold, 'reset_index'):
            Y_val_fold = Y_val_fold.reset_index(drop=True)
        X_test_encoded = X_test_encoded.reset_index(drop=True)
        Y_test = Y_test.reset_index(drop=True) if hasattr(Y_test, 'reset_index') else Y_test

        # Fit logistic regression
        logit_model = sm.Logit(Y_train_fold, X_train_encoded)
        result = logit_model.fit(disp=0)

        # Store coefficients
        fold_coefficients.append(result.params)

        # Predictions on test set (same test set for all folds, matching notebook)
        Y_test_pred_prob = result.predict(X_test_encoded)
        Y_test_pred = (Y_test_pred_prob > 0.5).astype(int)

        # Compute and store metrics on the held-out test set
        metrics = compute_metrics(Y_test, Y_test_pred, Y_test_pred_prob)
        fold_metrics.append(metrics)

        # Track best fold based on validation MCC
        Y_val_pred_prob = result.predict(X_val_encoded)
        Y_val_pred = (Y_val_pred_prob > 0.5).astype(int)
        val_metrics = compute_metrics(Y_val_fold, Y_val_pred, Y_val_pred_prob)

        if val_metrics['MCC'] > best_mcc:
            best_mcc = val_metrics['MCC']
            best_z_scores = pd.concat([
                result.summary2().tables[1]['z'],
                result.summary2().tables[1]['P>|z|']
            ], axis=1)
            best_z_scores.columns = ['z', 'p_value']
            best_fold = fold

        print(f"Fold {fold} completed")

    # Average metrics across folds
    metrics_df = pd.DataFrame(fold_metrics)
    avg_metrics = metrics_df.mean()
    std_metrics = metrics_df.std()

    print(f"\nAverage Metrics across {n_splits} folds:")
    print(f"  AUC: {avg_metrics['AUC']:.4f} ± {std_metrics['AUC']:.4f}")
    print(f"  F1:  {avg_metrics['F1']:.4f} ± {std_metrics['F1']:.4f}")
    print(f"  MCC: {avg_metrics['MCC']:.4f} ± {std_metrics['MCC']:.4f}")

    if best_z_scores is not None:
        print(f"\nTop 10 features by Z-score (from best fold {best_fold}):")
        print(best_z_scores.sort_values(by='z', key=abs, ascending=False).head(10))

    return {
        'auc': avg_metrics['AUC'],
        'f1': avg_metrics['F1'],
        'mcc': avg_metrics['MCC'],
        'auc_std': std_metrics['AUC'],
        'f1_std': std_metrics['F1'],
        'mcc_std': std_metrics['MCC'],
        'fold_metrics': fold_metrics,
        'model': None  # No single model in CV
    }

def run_xgboost(X_train, X_test, Y_train, Y_test):
    """
    Run XGBoost baseline.

    Uses XGBClassifier from xgboost library, matching the implementation in:
    - CardiomegalyBiomarkers/Cardiomegaly_Classification/XGBoost.ipynb
    """
    print("\n" + "=" * 80)
    print("Running XGBoost (XGBClassifier)")
    print("=" * 80)

    # Impute missing values
    imputer = SimpleImputer(strategy='mean')
    X_train_imputed = pd.DataFrame(
        imputer.fit_transform(X_train),
        columns=X_train.columns,
        index=X_train.index
    )
    X_test_imputed = pd.DataFrame(
        imputer.transform(X_test),
        columns=X_test.columns,
        index=X_test.index
    )

    # One-hot encode categorical variables
    if 'race_label' in X_train_imputed.columns:
        X_train_encoded = pd.get_dummies(
            X_train_imputed,
            columns=['race_label'],
            drop_first=True,
            dtype=float
        )
        X_test_encoded = pd.get_dummies(
            X_test_imputed,
            columns=['race_label'],
            drop_first=True,
            dtype=float
        )
        X_test_encoded = X_test_encoded.reindex(
            columns=X_train_encoded.columns,
            fill_value=0
        )
    else:
        X_train_encoded = X_train_imputed
        X_test_encoded = X_test_imputed

    # Train model using XGBClassifier (matching CardiomegalyBiomarkers/XGBoost.ipynb)
    # Parameters based on the notebook: eval_metric='logloss', scale_pos_weight=0.3/0.7,
    # colsample_bytree=0.75, gamma=0, learning_rate=0.1, subsample=0.75, max_depth=8
    model = XGBClassifier(
        eval_metric='logloss',
        scale_pos_weight=0.3/0.7,  # Based on CardiomegalyBiomarkers/XGBoost.ipynb
        colsample_bytree=0.75,
        gamma=0,
        learning_rate=0.1,
        subsample=0.75,
        max_depth=8,
        random_state=42,
        verbosity=1
    )
    model.fit(X_train_encoded, Y_train)

    # Predictions
    Y_test_pred_prob = model.predict_proba(X_test_encoded)[:, 1]
    Y_test_pred = model.predict(X_test_encoded)

    # Metrics
    auc = roc_auc_score(Y_test, Y_test_pred_prob)
    f1 = f1_score(Y_test, Y_test_pred)
    mcc = matthews_corrcoef(Y_test, Y_test_pred)
    cm = confusion_matrix(Y_test, Y_test_pred)

    print(f"\nResults:")
    print(f"  AUC: {auc:.4f}")
    print(f"  F1 Score: {f1:.4f}")
    print(f"  MCC: {mcc:.4f}")
    print(f"  Confusion Matrix:\n{cm}")

    # Feature importance (XGBoost has feature_importances_ attribute)
    feature_importance = pd.DataFrame({
        'feature': X_train_encoded.columns,
        'importance': model.feature_importances_
    }).sort_values('importance', ascending=False)

    print(f"\nTop 10 features by importance:")
    print(feature_importance.head(10))

    return {
        'auc': auc,
        'f1': f1,
        'mcc': mcc,
        'confusion_matrix': cm,
        'model': model,
        'feature_importance': feature_importance
    }



#### Run baseline tests

In [ ]:
# @title

"""
Run baseline comparisons using shallow ML models (logistic regression, XGBoost) on tabular/imaging features.
"""

results = {}

# Linear regression

# Prepare data for the "Tabular Data" runs
X_train, X_test, Y_train, Y_test, feature_cols = prepare_data(
    tabular_only=True
)

# Replicate by using average across 10-folds for logistic
results['Logistic Regression, Tabular Data'] = run_logistic_regression(X_train, X_test, Y_train, Y_test, n_splits=10)
results['XGBoost, Tabular Data'] = run_xgboost(X_train, X_test, Y_train, Y_test)

# Prepare data for the "Image Biomarkers + Tabular Data" runs (same except addition of two biomarker columns, CTR/CPAT)
X_train, X_test, Y_train, Y_test, feature_cols = prepare_data(
    tabular_only=False
)

# Replicate by using average across 10-folds for logistic
results['Logistic Regression, Image Biomarkers + Tabular Data'] = run_logistic_regression(X_train, X_test, Y_train, Y_test, n_splits=10)
results['XGBoost, Image Biomarkers + Tabular Data'] = run_xgboost(X_train, X_test, Y_train, Y_test)

# Prepare data for the "Image Biomarkers" runs (just two columns, CTR/CPAT)
X_train, X_test, Y_train, Y_test, feature_cols = prepare_data(
    tabular_only=False,
    idp_only=True
)

# Replicate by using average across 10-folds for logistic
results['Logistic Regression, Image Biomarkers'] = run_logistic_regression(X_train, X_test, Y_train, Y_test, n_splits=10)
results['XGBoost, Image Biomarkers'] = run_xgboost(X_train, X_test, Y_train, Y_test)

# Summary
print("\n" + "=" * 80)
print("Summary")
print("=" * 80)
for method_name, result in results.items():
    print(f"{method_name.upper()}:")
    print(f"  AUC: {result['auc']:.4f}")
    print(f"  F1:  {result['f1']:.4f}")
    print(f"  MCC: {result['mcc']:.4f}")

Total samples: 2662
Train samples: 2129, Test samples: 533
Fold 1 completed
Fold 2 completed
Fold 3 completed
Fold 4 completed
Fold 5 completed
Fold 6 completed
Fold 7 completed
Fold 8 completed
Fold 9 completed
Fold 10 completed

Average Metrics across 10 folds:
  AUC: 0.6985 ± 0.0019
  F1:  0.8232 ± 0.0012
  MCC: 0.1926 ± 0.0107

Top 10 features by Z-score (from best fold 9):
                            z       p_value
age_label            6.837647  8.050471e-12
Urea_Nitrogren_mean  3.364635  7.664507e-04
Magnesium_mean       2.782741  5.390174e-03
Chloride_mean       -2.444045  1.452361e-02
Phosphate_mean       2.050037  4.036080e-02
Hematocrit_mean      1.560060  1.187456e-01
RR_mean              0.473538  6.358295e-01
const               -0.433495  6.646552e-01
Glucose_mean         0.339385  7.343200e-01

Running XGBoost (XGBClassifier)

Results:
  AUC: 0.6398
  F1 Score: 0.7623
  MCC: 0.1907
  Confusion Matrix:
[[ 67  93]
 [ 86 287]]

Top 10 features by importance:
              

#### Copied results table from Barttender paper to compare

```
Results from Barttender PDF:

LOGISTIC REGRESSION, TABULAR DATA:
  AUC: 0.70
  F1:  0.82
  MCC: 0.19
XGBOOST, TABULAR DATA:
  AUC: 0.64
  F1:  0.74
  MCC: 0.21
LOGISTIC REGRESSION, IMAGE BIOMARKERS + TABULAR DATA:
  AUC: 0.88
  F1:  0.89
  MCC: 0.61
XGBOOST, IMAGE BIOMARKERS + TABULAR DATA:
  AUC: 0.83
  F1:  0.88
  MCC: 0.63
LOGISTIC REGRESSION, IMAGE BIOMARKERS:
  AUC: 0.88
  F1:  0.89
  MCC: 0.60
XGBOOST, IMAGE BIOMARKERS:
  AUC: 0.85
  F1:  0.88
  MCC: 0.65
```
Note that they are pretty similar, a bit of variance with XGBoost. For XGBoost, barttender did not include any code (it is assumed that they used the Cardiomegaly repo scripts as-is) so it could account for the small differences since the paper mentions some modification to the XGB classification parameters. Could also result from random variance from 10 fold average, different training/test splits, etc. It is "close enough".


# Barttender Experiment

In [ ]:
from mimic_add_bar_preprocess import preprocess_mimic_df, preprocess_only_bars, preprocess_and_append_bars
from mimic_constants import *

## Process a single sample (index i=1)
i = 1
df_cxr = preprocess_mimic_df(idp=True, verbose=False, bar_vars=lr_variables_all) # we can use significant_variables here also for just the 8 selected features
preprocess_only_bars(df_cxr[i:i+1], img_data_dir=nb_group_dir, verbose=True)

ModuleNotFoundError: No module named 'mimic_add_bar_preprocess'

In [ ]:
preprocess_and_append_bars(df_cxr[i:i+1], image_type='blank', img_data_dir=nb_group_dir, verbose=True)

In [ ]:
preprocess_and_append_bars(df_cxr[i:i+1], image_type='xray', img_data_dir=nb_group_dir, verbose=True)

#### Replicating full Barttender experiments below - more time intensive

In [ ]:
from mimic_add_bar_preprocess import preprocess_mimic_df, preprocess_only_bars, preprocess_and_append_bars, preprocess_no_bars
from mimic_constants import *

# Preprocess all with 8 significant features
df_cxr = preprocess_mimic_df(idp=True, verbose=True, bar_vars=significant_variables)

In [ ]:
import os
from mimic_constants import nb_group_dir

# Ensure the directory exists
os.makedirs(nb_group_dir, exist_ok=True)
print(f"Ensured directory exists: {nb_group_dir}")


In [ ]:
# Image Barttender processing (xray + bars) - will take around 45 minutes
preprocess_and_append_bars(
    df_cxr,
    image_type='xray',
    img_data_dir=nb_group_dir,
    idp=True,
    bar_vars=significant_variables,
    verbose=False # IMPORTANT: it won't save the images if you run in verbose mode
)

In [ ]:
# Blank barttender (black image + bars)
preprocess_and_append_bars(
    df_cxr,
    image_type='blank',
    img_data_dir=nb_group_dir,
    idp=True,
    order=None,
    bar_vars=significant_variables,
    verbose=False
)

NameError: name 'preprocess_and_append_bars' is not defined

In [ ]:
torch.cuda.is_available()

True

In [ ]:
# Image only
preprocess_no_bars(
    df_cxr,
    out_dir=nb_group_dir,
    verbose=False
)

In [ ]:
import importlib
import os
import wandb
os.environ['WANDB_MODE'] = 'offline'
!export WANDB_MODE=offline
importlib.reload(wandb)
import wandb

!wandb offline

from mimic_k_fold import main as train_main
train_main(
    image_type='xray',
    batch_size=32,
    epochs=100,
    n_splits=10,
    idp=True,
    num_workers=4
)

W&B offline. Running your script from this directory will only write metadata locally. Use wandb disabled to completely turn off W&B.


INFO:lightning_fabric.utilities.seed:Seed set to 42
Loading Data: 100%|██████████| 537/537 [00:00<00:00, 53141.31it/s]
/usr/local/lib/python3.12/dist-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/usr/local/lib/python3.12/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=DenseNet121_Weights.IMAGENET1K_V1`. You can also use `weights=DenseNet121_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


#train:  1849
#val:    276
#test:   537
Optimal batch size found: 32

--- Fold 1/10 ---
Downloading: "https://download.pytorch.org/models/densenet121-a639ec97.pth" to /root/.cache/torch/hub/checkpoints/densenet121-a639ec97.pth


100%|██████████| 30.8M/30.8M [00:00<00:00, 216MB/s]
/usr/local/lib/python3.12/dist-packages/notebook/notebookapp.py:191: SyntaxWarning: invalid escape sequence '\/'
  | |_| | '_ \/ _` / _` |  _/ -_)
wandb: WARNING `resume` will be ignored since W&B syncing is set to `offline`. Starting a new run with run id uy0ubpnf.


INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
/usr/local/lib/python3.12/dist-packages/torch/__init__.py:1551: UserWarning: Please use the new API settings to control TF32 behavior, such as torch.backends.cudnn.conv.fp32_precision = 'tf32' or torch.backends.cuda.matmul.fp32_precision = 'ieee'. Old settings, e.g, torch.backends.cuda.matmul.allow_tf32 = True, torch.backends.cudnn.allow_tf32 = True, allowTF32CuDNN() and allowTF32CuBLAS() will be deprecated after Pytorch 2.9. Please see https://pytorch.org/docs/main/notes/cuda.html#tensorfloat-32-tf32-on-ampere-and-later-devices (Triggered internally at /pytorch/aten/src/ATen/Context.cpp:80.)
  return _C._get_float32_matmul_precision()
INFO:pytorch_lightning.utilities.rank_zero:You are using a CUDA device ('NVIDIA A100-SXM4-80GB') that has Tensor Cores. To properly utilize them, you should set `torch.set_float32_matmul_pre

...

Test-loop: 100%|██████████| 6/6 [00:00<00:00,  6.00it/s]


Cardiomegaly AUC: 0.7818

TESTING for Fold 10


Test-loop: 100%|██████████| 17/17 [00:01<00:00, 10.40it/s]


Cardiomegaly AUC: 0.8710



Mean Validation Metrics across 10 folds: {'AUC': np.float64(0.7832894687491794), 'Average Precision': np.float64(0.8923672766542458), 'TPR': np.float64(0.9250955559211504), 'TNR': np.float64(0.3777031748853076), 'PPV': np.float64(0.7744345785453517), 'NPV': np.float64(0.7088868761423927), 'F1': np.float64(0.8425853080460011), 'MCC': np.float64(0.3800377981191999)}

Mean Test Metrics across 10 folds: {'AUC': np.float64(0.8673275862068965), 'Average Precision': np.float64(0.9345304166786217), 'TPR': np.float64(0.8923076923076924), 'TNR': np.float64(0.590625), 'PPV': np.float64(0.8412324597067471), 'NPV': np.float64(0.7202770792290514), 'F1': np.float64(0.8632801446543302), 'MCC': np.float64(0.5178549999954509)}

Best folds based on validation metrics: {'AUC': 4, 'Average Precision': 4, 'TPR': 9, 'TNR': 8, 'PPV': 4, 'NPV': 9, 'F1': 4, 'MCC': 4}


In [ ]:
import importlib
import os
import wandb
os.environ['WANDB_MODE'] = 'offline'
!export WANDB_MODE=offline
importlib.reload(wandb)
import wandb

!wandb offline

from mimic_k_fold import main as train_main
train_main(
    image_type='blank',
    batch_size=32,
    epochs=100,
    n_splits=10,
    idp=True,
    num_workers=4
)

W&B offline. Running your script from this directory will only write metadata locally. Use wandb disabled to completely turn off W&B.


INFO:lightning_fabric.utilities.seed:Seed set to 42
Loading Data: 100%|██████████| 537/537 [00:00<00:00, 53220.42it/s]
/usr/local/lib/python3.12/dist-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/usr/local/lib/python3.12/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=DenseNet121_Weights.IMAGENET1K_V1`. You can also use `weights=DenseNet121_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


#train:  1849
#val:    276
#test:   537
Optimal batch size found: 32

--- Fold 1/10 ---


wandb: WARNING `resume` will be ignored since W&B syncing is set to `offline`. Starting a new run with run id vl2rylge.


INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name  | Type     | Params | Mode 
-------------------------------------------
0 | model | DenseNet | 7.0 M  | train
-------------------------------------------
7.0 M     Trainable params
0         Non-trainable params
7.0 M     Total params
27.820    Total estimated model params size (MB)
433       Modules in train mode
0         Modules in eval mode


...

Test-loop: 100%|██████████| 6/6 [00:01<00:00,  5.96it/s]


Cardiomegaly AUC: 0.6803

TESTING for Fold 10


Test-loop: 100%|██████████| 17/17 [00:01<00:00,  9.37it/s]

Cardiomegaly AUC: 0.7190



Mean Validation Metrics across 10 folds: {'AUC': np.float64(0.6666455115030029), 'Average Precision': np.float64(0.8111744655612128), 'TPR': np.float64(0.9681903808638891), 'TNR': np.float64(0.06904974388417526), 'PPV': np.float64(0.7062252286275206), 'NPV': np.float64(0.4191758241758242), 'F1': np.float64(0.8159819380900204), 'MCC': np.float64(0.07226978292989313)}

Mean Test Metrics across 10 folds: {'AUC': np.float64(0.7146933023872679), 'Average Precision': np.float64(0.8393992240335784), 'TPR': np.float64(0.9644562334217508), 'TNR': np.float64(0.13874999999999998), 'PPV': np.float64(0.7267756541156554), 'NPV': np.float64(0.6431395079502433), 'F1': np.float64(0.8279344850089376), 'MCC': np.float64(0.1720723682532801)}

Best folds based on validation metrics: {'AUC': 1, 'Average Precision': 4, 'TPR': 3, 'TNR': 1, 'PPV': 4, 'NPV': 8, 'F1': 4, 'MCC': 1}


In [ ]:
# TODO clean these imports up, I was just trying everything I could to get the wandb server to stop asking for an API key
import importlib
import os
import wandb
os.environ['WANDB_MODE'] = 'offline'
!export WANDB_MODE=offline
importlib.reload(wandb)
import wandb

!wandb offline

from mimic_k_fold import main as train_main
train_main(
    image_type='xray',
    batch_size=32,
    epochs=100,
    n_splits=10,
    idp=True,
    num_workers=4,
    no_bars=True
)

W&B offline. Running your script from this directory will only write metadata locally. Use wandb disabled to completely turn off W&B.


INFO:lightning_fabric.utilities.seed:Seed set to 42
Loading Data: 100%|██████████| 537/537 [00:00<00:00, 38885.09it/s]
/usr/local/lib/python3.12/dist-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/usr/local/lib/python3.12/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=DenseNet121_Weights.IMAGENET1K_V1`. You can also use `weights=DenseNet121_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


#train:  1849
#val:    276
#test:   537
Optimal batch size found: 32

--- Fold 1/10 ---


wandb: WARNING `resume` will be ignored since W&B syncing is set to `offline`. Starting a new run with run id 1h4bt3g6.


INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name  | Type     | Params | Mode 
-------------------------------------------
0 | model | DenseNet | 7.0 M  | train
-------------------------------------------
7.0 M     Trainable params
0         Non-trainable params
7.0 M     Total params
27.820    Total estimated model params size (MB)
433       Modules in train mode
0         Modules in eval mode


...

Test-loop: 100%|██████████| 6/6 [00:01<00:00,  5.54it/s]


Cardiomegaly AUC: 0.7566

TESTING for Fold 10


Test-loop: 100%|██████████| 17/17 [00:01<00:00,  9.53it/s]


Cardiomegaly AUC: 0.8515



Mean Validation Metrics across 10 folds: {'AUC': np.float64(0.7652880549479061), 'Average Precision': np.float64(0.8797189927754824), 'TPR': np.float64(0.9396367456522391), 'TNR': np.float64(0.3284871085775512), 'PPV': np.float64(0.7670759611886113), 'NPV': np.float64(0.767327254883934), 'F1': np.float64(0.8434417971652632), 'MCC': np.float64(0.36397931736462813)}

Mean Test Metrics across 10 folds: {'AUC': np.float64(0.8576027851458885), 'Average Precision': np.float64(0.9304875909118472), 'TPR': np.float64(0.8891246684350133), 'TNR': np.float64(0.541875), 'PPV': np.float64(0.8291038833813967), 'NPV': np.float64(0.7158492528727671), 'F1': np.float64(0.8527323724315459), 'MCC': np.float64(0.47355840330776333)}

Best folds based on validation metrics: {'AUC': 8, 'Average Precision': 8, 'TPR': 2, 'TNR': 8, 'PPV': 8, 'NPV': 2, 'F1': 4, 'MCC': 8}


In [ ]:
experiments = [
    "densenet-xray-age_chloride_rr_urea_nitrogren_magnesium_glucose_phosphate_hematocrit-idp",
    "densenet-blank-age_chloride_rr_urea_nitrogren_magnesium_glucose_phosphate_hematocrit-idp",
    "densenet-xray-no_bars-idp",
]

comparison_results = []
exp_base_dir = home_out_dir / "cross-val"

for exp_name in experiments:
    exp_dir = exp_base_dir / exp_name
    if not exp_dir.exists():
        print(str(exp_dir) + " doesn't exist")
        continue
    print("---")
    print(exp_name)
    print("---")
    print(pd.read_csv(exp_dir / "metrics_summary.csv"))

---
densenet-xray-age_chloride_rr_urea_nitrogren_magnesium_glucose_phosphate_hematocrit-idp
---
              metric  val_mean   val_std  test_mean  test_std  best_fold
0                AUC  0.783289  0.028326   0.867328  0.014699          4
1  Average Precision  0.892367  0.025043   0.934530  0.012126          4
2                TPR  0.925096  0.039476   0.892308  0.059669          9
3                TNR  0.377703  0.079048   0.590625  0.137422          8
4                PPV  0.774435  0.030754   0.841232  0.039115          4
5                NPV  0.708887  0.096218   0.720277  0.067992          9
6                 F1  0.842585  0.027897   0.863280  0.012767          4
7                MCC  0.380038  0.066973   0.517855  0.042222          4
---
densenet-blank-age_chloride_rr_urea_nitrogren_magnesium_glucose_phosphate_hematocrit-idp
---
              metric  val_mean   val_std  test_mean  test_std  best_fold
0                AUC  0.666646  0.042830   0.714693  0.014140          1
1  A

Extension (Trying out different variable selection method to improve barttender performance)

In [ ]:
# loading master non-idf dataframe
import pandas as pd
df_master = pd.read_pickle(feature_folder / 'MIMIC_features_v3.pkl')
df_master.shape

(22982, 102)

In [ ]:
# be sure to run labels cell before this

indexing_cols = ['subject_id', 'study_id']
imaging_cols  = ['ViewPosition', 'path']
icu_cols = ['hadm_id', 'stay_id', 'first_careunit', 'last_careunit', 'intime', 'outtime', 'los', 'Match',\
    'EarlyBoundary', 'PostGapStart', 'PostGapStop']
label_cols = ['No Finding', 'Enlarged Cardiomediastinum', 'Cardiomegaly', 'Lung Opacity', 'Lung Lesion', \
    'Edema', 'Consolidation', 'Pneumonia', 'Atelectasis', 'Pneumothorax', 'Pleural Effusion', 'Pleural Other',\
    'Fracture', 'Support Devices']
demographic_cols = ['ethnicity', 'anchor_age', 'anchor_year', 'gender']
chart_labels_mean_cols = list(chart_labels_mean.values())
chart_labels_max_cols  = list(chart_labels_max.values())
chart_labels_min_cols  = list(chart_labels_min.values())
lab_labels_mean_cols   = list(lab_labels_mean.values())
lab_labels_max_cols    = list(lab_labels_max.values())
lab_labels_min_cols    = list(lab_labels_min.values())

In [ ]:
# removing columns with too many NaNs
df = df_master
select_col_groups = []
removed_col_groups = []
og_col_groups = [chart_labels_mean_cols, chart_labels_max_cols, chart_labels_min_cols, lab_labels_mean_cols, lab_labels_max_cols, lab_labels_min_cols]
for col_group in og_col_groups:
    nan_counts = df_master[col_group].isna().sum()
    too_many_nans = nan_counts[nan_counts > 1000].index.tolist()
    df = df.drop(too_many_nans, axis=1)
    col_group = list(set(col_group) - set(too_many_nans))
    select_col_groups.append(col_group)
    removed_col_groups.append(too_many_nans)

In [ ]:
select_col_groups

[['NBPd_mean',
  'HR_mean',
  'RR_mean',
  'SpO2_mean',
  'PlateletCount_mean',
  'Temp(F)_mean',
  'Sodium_mean',
  'NBPm_mean',
  'NBPs_mean'],
 ['Sodium_max', 'HR_max', 'NBPm_max', 'NBPs_max', 'NBPd_max', 'RR_max'],
 ['NBPs_min',
  'SpO2_min',
  'NBPd_min',
  'HR_min',
  'RR_min',
  'NBPm_min',
  'Sodium_min'],
 ['Potassium_mean',
  'Hematocrit_mean',
  'Phosphate_mean',
  'Creatinine_mean',
  'Magnesium_mean',
  'Urea_Nitrogren_mean',
  'Calcium_Total_mean',
  'Chloride_mean',
  'Glucose_mean'],
 ['Potassium_max'],
 ['Potassium_min']]

In [ ]:
removed_col_groups

[['ABPm_mean',
  'ABPd_mean',
  'ABPs_mean',
  'FiO2_mean',
  'PH_mean',
  'PCO2_mean',
  'SaO2_mean',
  'Albumin_mean',
  'Cholesterol_mean',
  'PO2_mean'],
 ['ABPm_max', 'ABPd_max', 'ABPs_max', 'FiO2_max', 'PCO2_max'],
 ['ABPm_min', 'ABPd_min', 'ABPs_min', 'PCO2_min'],
 ['Tidal_Volume_mean',
  'Alkaline_Phosphatase_mean',
  'Lactate_mean',
  'Bilirubin',
  'Troponin-T_mean',
  'Hemoglobin_mean',
  'ALT_mean',
  'PTT_mean',
  'WBC_mean',
  'Fibrinogen'],
 ['Troponin-T_max', 'Hemoglobin_max', 'WBC_max'],
 ['Hemoglobin_min', 'WBC_min']]

Prepping Data for Cardiomegaly (Copying preprocessing method done in mimic-lr-no-idp.ipynb)

In [ ]:
# Import functions
import pandas as pd
import numpy as np
from pathlib import Path
from sklearn.ensemble import HistGradientBoostingClassifier
from sklearn.model_selection import train_test_split
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler
import statsmodels.api as sm
from sklearn.metrics import roc_auc_score, f1_score, confusion_matrix

label = 'Cardiomegaly'
df = df[df[label].isin([0, 1])]  # pick only positive and negative samples from label
f'Number of Total Samples: {len(df)}'

'Number of Total Samples: 11423'

In [ ]:
df.columns

Index(['subject_id', 'hadm_id', 'stay_id', 'first_careunit', 'last_careunit',
       'intime', 'outtime', 'los', 'Match', 'study_id', 'No Finding',
       'Enlarged Cardiomediastinum', 'Cardiomegaly', 'Lung Opacity',
       'Lung Lesion', 'Edema', 'Consolidation', 'Pneumonia', 'Atelectasis',
       'Pneumothorax', 'Pleural Effusion', 'Pleural Other', 'Fracture',
       'Support Devices', 'ViewPosition', 'path', 'EarlyBoundary',
       'PostGapStart', 'PostGapStop', 'StudyDate', 'split', 'ethnicity',
       'anchor_age', 'anchor_year', 'gender', 'HR_mean', 'NBPs_mean',
       'NBPd_mean', 'NBPm_mean', 'RR_mean', 'SpO2_mean', 'Sodium_mean',
       'Temp(F)_mean', 'PlateletCount_mean', 'HR_max', 'NBPs_max', 'NBPd_max',
       'NBPm_max', 'RR_max', 'Sodium_max', 'HR_min', 'NBPs_min', 'NBPd_min',
       'NBPm_min', 'RR_min', 'SpO2_min', 'Sodium_min', 'Calcium_Total_mean',
       'Chloride_mean', 'Creatinine_mean', 'Glucose_mean', 'Magnesium_mean',
       'Phosphate_mean', 'Potassium_mean', 

In [ ]:

study_year = np.floor(df['StudyDate'] / 10000)
delta_years = study_year - df['anchor_year']
df['age'] = df['anchor_age'] + delta_years
df['age_label'] = df['age'] / 100

df['age_label'] = df['age'] / 100

df['race_label'] = df['ethnicity']
df.loc[df['race_label'] == 'White', 'race_label'] = 0
df.loc[df['race_label'] == 'Asian', 'race_label'] = 1
df.loc[df['race_label'] == 'Black', 'race_label'] = 2
df.loc[df['race_label'] == 'Hispanic/Latino', 'race_label'] = 3
df.loc[df['race_label'] == 'Other', 'race_label'] = 4

df['sex_label'] = df['gender']
df.loc[df['sex_label'] == 'M', 'sex_label'] = 0
df.loc[df['sex_label'] == 'F', 'sex_label'] = 1

demographic_cols = ['age_label', 'race_label', 'sex_label']

X = df[['split'] + demographic_cols + select_col_groups[0] + select_col_groups[3]]
Y = df[['split'] + [label]]
X_train = X[X['split'] == 'train'].drop(['split'], axis=1)
Y_train = Y[Y['split'] == 'train'].drop(['split'], axis=1)[label].astype(float)
X_test = X[X['split'] == 'test'].drop(['split'], axis=1)
Y_test = Y[Y['split'] == 'test'].drop(['split'], axis=1)[label].astype(float)

In [ ]:
# 1. Adjust Train-Test Split to 90/10
# Calculate the number of samples to move from train to test
additional_test_samples = 916

# Sampling additional samples from X_train and Y_train
X_train_to_test, X_train = train_test_split(X_train, test_size=(11110 - additional_test_samples) / 11110, random_state=42, stratify=Y_train)
Y_train_to_test, Y_train = train_test_split(Y_train, test_size=(11110 - additional_test_samples) / 11110, random_state=42, stratify=Y_train)

# Concatenate the sampled data to the test sets
X_test = pd.concat([X_test, X_train_to_test], axis=0)
Y_test = pd.concat([Y_test, Y_train_to_test], axis=0)

In [ ]:
# 2. Mean Imputation for NaNs in X_train
imputer = SimpleImputer(strategy='mean')
X_train_imputed = pd.DataFrame(imputer.fit_transform(X_train), columns=X_train.columns)
X_test_imputed = pd.DataFrame(imputer.transform(X_test), columns=X_test.columns)

# 3. One-Hot Encoding for 'race_label'
X_train_encoded = pd.get_dummies(X_train_imputed, columns=['race_label'], drop_first=True, dtype=float)
X_test_encoded = pd.get_dummies(X_test_imputed, columns=['race_label'], drop_first=True, dtype=float)

# Ensure that the train and test sets have the same columns after encoding
X_test_encoded = X_test_encoded.reindex(columns=X_train_encoded.columns, fill_value=0)

X_train_encoded = sm.add_constant(X_train_encoded)  # Add intercept term
X_test_encoded = sm.add_constant(X_test_encoded)

X_train_encoded = X_train_encoded.reset_index(drop=True)
X_test_encoded = X_test_encoded.reset_index(drop=True)
Y_train = Y_train.reset_index(drop=True)
Y_test = Y_test.reset_index(drop=True)

In [ ]:
X_train.columns

Index(['age_label', 'race_label', 'sex_label', 'NBPd_mean', 'HR_mean',
       'RR_mean', 'SpO2_mean', 'PlateletCount_mean', 'Temp(F)_mean',
       'Sodium_mean', 'NBPm_mean', 'NBPs_mean', 'Potassium_mean',
       'Hematocrit_mean', 'Phosphate_mean', 'Creatinine_mean',
       'Magnesium_mean', 'Urea_Nitrogren_mean', 'Calcium_Total_mean',
       'Chloride_mean', 'Glucose_mean'],
      dtype='object')

In [ ]:
X_train_encoded.columns

Index(['const', 'age_label', 'sex_label', 'NBPd_mean', 'HR_mean', 'RR_mean',
       'SpO2_mean', 'PlateletCount_mean', 'Temp(F)_mean', 'Sodium_mean',
       'NBPm_mean', 'NBPs_mean', 'Potassium_mean', 'Hematocrit_mean',
       'Phosphate_mean', 'Creatinine_mean', 'Magnesium_mean',
       'Urea_Nitrogren_mean', 'Calcium_Total_mean', 'Chloride_mean',
       'Glucose_mean', 'race_label_1.0', 'race_label_2.0', 'race_label_3.0',
       'race_label_4.0'],
      dtype='object')

LASSO Regression as extended variable selection method

In [ ]:
# Importing LassoCV so that best alpha coefficient is found via cross-validation
from sklearn.linear_model import LassoCV
lasso_cv = LassoCV(cv=10)
lasso_cv.fit(X_train_encoded, Y_train)


LassoCV(cv=10)

In [ ]:
# predictions and evaluations
from sklearn.metrics import roc_auc_score, f1_score, confusion_matrix
Y_pred_prob = lasso_cv.predict(X_test_encoded)
Y_pred = (Y_pred_prob > 0.5).astype(int)

auc_score = roc_auc_score(Y_test, Y_pred_prob)
f1 = f1_score(Y_test, Y_pred)
conf_matrix = confusion_matrix(Y_test, Y_pred)

In [ ]:
print(f'AUC: {auc_score}', f'F1 Score: {f1}', f'Confusion Matrix:\n{conf_matrix}', sep='\n')

AUC: 0.7036981084568659
F1 Score: 0.4713216957605985
Confusion Matrix:
[[520 103]
 [321 189]]


In [ ]:
# Finding which features have nonzero coefficients (indicating significance)
nonzero_indices = np.where(lasso_cv.coef_ != 0)[0]
nonzero_indices

array([ 3,  4,  5,  6,  7,  8,  9, 10, 13, 17, 19, 20])

In [ ]:
X_train_encoded.columns

Index(['const', 'age_label', 'sex_label', 'NBPd_mean', 'HR_mean', 'RR_mean',
       'SpO2_mean', 'PlateletCount_mean', 'Temp(F)_mean', 'Sodium_mean',
       'NBPm_mean', 'NBPs_mean', 'Potassium_mean', 'Hematocrit_mean',
       'Phosphate_mean', 'Creatinine_mean', 'Magnesium_mean',
       'Urea_Nitrogren_mean', 'Calcium_Total_mean', 'Chloride_mean',
       'Glucose_mean', 'race_label_1.0', 'race_label_2.0', 'race_label_3.0',
       'race_label_4.0'],
      dtype='object')

In [ ]:
X_train_encoded.columns[nonzero_indices]

Index(['NBPd_mean', 'HR_mean', 'RR_mean', 'SpO2_mean', 'PlateletCount_mean',
       'Temp(F)_mean', 'Sodium_mean', 'NBPm_mean', 'Hematocrit_mean',
       'Urea_Nitrogren_mean', 'Chloride_mean', 'Glucose_mean'],
      dtype='object')

In [ ]:
# Features selected by LASSO:
lasso_significant_variables = ['NBPd_mean', 'Temp(F)_mean', 'NBPm_mean', 'Sodium_mean',
       'PlateletCount_mean', 'RR_mean', 'HR_mean', 'SpO2_mean',
       'Hematocrit_mean', 'Chloride_mean', 'Urea_Nitrogren_mean',
       'Glucose_mean']

Recreating Main Barttender Experiment (Images + Bars) with New Significant Variables

In [ ]:
from mimic_add_bar_preprocess import preprocess_mimic_df, preprocess_only_bars, preprocess_and_append_bars, preprocess_no_bars
from mimic_constants import *

# Preprocess all with new 12 significant features
df_cxr_ex = preprocess_mimic_df(idp=True, verbose=True, bar_vars=lasso_significant_variables)

                                                path  ...  Glucose_mean
0  files/p10/p10001884/s55333410/5b135035-4708084...  ...      0.773585
1  files/p10/p10002013/s52163036/1e647043-eed3576...  ...      0.893887
2  files/p10/p10004457/s55439624/ad41d9ed-37ff140...  ...      0.247247
3  files/p10/p10011365/s56594284/ff295ca5-9f888b5...  ...      0.717168
4  files/p10/p10012292/s52412975/ca16ea39-8c22bfd...  ...      0.662663

[5 rows x 13 columns]
[['NBPd_mean', 'Temp(F)_mean', 'NBPm_mean', 'Sodium_mean', 'PlateletCount_mean', 'RR_mean', 'HR_mean', 'SpO2_mean', 'Hematocrit_mean', 'Chloride_mean', 'Urea_Nitrogren_mean', 'Glucose_mean']]


In [ ]:
import os
from mimic_constants import nb_group_dir

# Ensure the directory exists
os.makedirs(nb_group_dir, exist_ok=True)
print(f"Ensured directory exists: {nb_group_dir}")


Ensured directory exists: /content/drive/MyDrive/physionet.org/files/mimic-cxr-jpg/2.1.0/preprocessed


In [ ]:
# Image Barttender processing (xray + bars) - will take around 45 minutes
preprocess_and_append_bars(
    df_cxr_ex,
    image_type='xray',
    img_data_dir=nb_group_dir,
    idp=True,
    bar_vars=lasso_significant_variables,
    verbose=False # IMPORTANT: it won't save the images if you run in verbose mode
)

Image Type: xray
Barcode Order: nbpd, temp(f), nbpm, sodium, plateletcount, rr, hr, spo2, hematocrit, chloride, urea, nitrogren, glucose
preproc_dir: /content/drive/MyDrive/physionet.org/files/mimic-cxr-jpg/2.1.0/preprocessed/preproc_224x224_xray_nbpd_temp(f)_nbpm_sodium_plateletcount_rr_hr_spo2_hematocrit_chloride_urea_nitrogren_glucose


100%|██████████| 2662/2662 [55:18<00:00,  1.25s/it]


In [ ]:
import importlib
import os
import wandb
os.environ['WANDB_MODE'] = 'offline'
!export WANDB_MODE=offline
importlib.reload(wandb)
import wandb

!wandb offline

from mimic_k_fold import main as train_main
train_main(
    image_type='xray',
    batch_size=32,
    epochs=100,
    n_splits=10,
    idp=True,
    num_workers=4
)

W&B offline. Running your script from this directory will only write metadata locally. Use wandb disabled to completely turn off W&B.


INFO:lightning_fabric.utilities.seed:Seed set to 42
Loading Data: 100%|██████████| 537/537 [00:00<00:00, 53428.72it/s]
/usr/local/lib/python3.12/dist-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/usr/local/lib/python3.12/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=DenseNet121_Weights.IMAGENET1K_V1`. You can also use `weights=DenseNet121_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


#train:  1849
#val:    276
#test:   537
Optimal batch size found: 32

--- Fold 1/10 ---
Downloading: "https://download.pytorch.org/models/densenet121-a639ec97.pth" to /root/.cache/torch/hub/checkpoints/densenet121-a639ec97.pth


100%|██████████| 30.8M/30.8M [00:00<00:00, 231MB/s]
/usr/local/lib/python3.12/dist-packages/notebook/notebookapp.py:191: SyntaxWarning: invalid escape sequence '\/'
  | |_| | '_ \/ _` / _` |  _/ -_)
wandb: WARNING `resume` will be ignored since W&B syncing is set to `offline`. Starting a new run with run id 22t1xjm0.


INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


...

Test-loop: 100%|██████████| 6/6 [00:01<00:00,  5.06it/s]


Cardiomegaly AUC: 0.7501

TESTING for Fold 10


Test-loop: 100%|██████████| 17/17 [00:02<00:00,  8.00it/s]

Cardiomegaly AUC: 0.8788



Mean Validation Metrics across 10 folds: {'AUC': np.float64(0.7917972173522776), 'Average Precision': np.float64(0.89348918723801), 'TPR': np.float64(0.9266781453702398), 'TNR': np.float64(0.41086720957848727), 'PPV': np.float64(0.7854481889942733), 'NPV': np.float64(0.7087457971174296), 'F1': np.float64(0.8492485826764739), 'MCC': np.float64(0.40637062985134376)}

Mean Test Metrics across 10 folds: {'AUC': np.float64(0.8681896551724136), 'Average Precision': np.float64(0.936753554415177), 'TPR': np.float64(0.8835543766578249), 'TNR': np.float64(0.616875), 'PPV': np.float64(0.8489774545669748), 'NPV': np.float64(0.7174327522403583), 'F1': np.float64(0.8625403731273782), 'MCC': np.float64(0.5292011225841229)}

Best folds based on validation metrics: {'AUC': 8, 'Average Precision': 4, 'TPR': 1, 'TNR': 6, 'PPV': 4, 'NPV': 1, 'F1': 4, 'MCC': 1}


In [ ]:
experiments = [
    "densenet-xray-age_chloride_rr_urea_nitrogren_magnesium_glucose_phosphate_hematocrit-idp",
    "densenet-xray-nbpd_temp(f)_nbpm_sodium_plateletcount_rr_hr_spo2_hematocrit_chloride_urea_nitrogren_glucose-idp",
    "densenet-blank-age_chloride_rr_urea_nitrogren_magnesium_glucose_phosphate_hematocrit-idp",
    "densenet-xray-no_bars-idp",
]

comparison_results = []
exp_base_dir = home_out_dir / "cross-val"

for exp_name in experiments:
    exp_dir = exp_base_dir / exp_name
    if not exp_dir.exists():
        print(str(exp_dir) + " doesn't exist")
        continue
    print("---")
    print(exp_name)
    print("---")
    print(pd.read_csv(exp_dir / "metrics_summary.csv"))

---
densenet-xray-age_chloride_rr_urea_nitrogren_magnesium_glucose_phosphate_hematocrit-idp
---
              metric  val_mean   val_std  test_mean  test_std  best_fold
0                AUC  0.783289  0.028326   0.867328  0.014699          4
1  Average Precision  0.892367  0.025043   0.934530  0.012126          4
2                TPR  0.925096  0.039476   0.892308  0.059669          9
3                TNR  0.377703  0.079048   0.590625  0.137422          8
4                PPV  0.774435  0.030754   0.841232  0.039115          4
5                NPV  0.708887  0.096218   0.720277  0.067992          9
6                 F1  0.842585  0.027897   0.863280  0.012767          4
7                MCC  0.380038  0.066973   0.517855  0.042222          4
---
densenet-xray-nbpd_temp(f)_nbpm_sodium_plateletcount_rr_hr_spo2_hematocrit_chloride_urea_nitrogren_glucose-idp
---
              metric  val_mean   val_std  test_mean  test_std  best_fold
0                AUC  0.791797  0.052906   0.868190  0.